In [1]:
import pandas as pd
import numpy as np
import pyunpack
import math
import json

from models import GatedLinearUnit
from models import GateAddNormNetwork
from models import GatedResidualNetwork 
from models import ScaledDotProductAttention
from models import InterpretableMultiHeadAttention
from models import VariableSelectionNetwork

#from data_formatters.m5_faster import M5Formatter
from datasets.M5dataset import TFTDataset
from data_formatters.base import GenericDataFormatter
from data_formatters.base import DataTypes, InputTypes

from quantile_loss import QuantileLossCalculator
from quantile_loss import NormalizedQuantileLossCalculator

import torch
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torch import nn

import pytorch_lightning as pl
from pytorch_lightning.callbacks import EarlyStopping
from argparse import ArgumentParser

import matplotlib.pyplot as plt
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler

In [2]:
from utils.utils import get_single_col_by_input_type
from utils.utils import extract_cols_from_data_type

from data_formatters.base import DataTypes, InputTypes

In [2]:
import pandas as pd
import modin.pandas as mpd
import dask.dataframe as dd
import numpy as np
import cudf
import dask_cudf
import sklearn
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
#from dask_ml.preprocessing import LabelEncoder
#from dask_ml.preprocessing import StandardScaler

In [3]:
import os
os.environ["MODIN_OUT_OF_CORE"] = 'true'
os.environ["MODIN_MEMORY"] = '100000000000'

## Creating Datasets

In [3]:
#m5_data = pd.read_pickle('/home/daniel/github/kaggle_competitions/M5_Forecasting_Accuracy/data/full_data.pkl')
m5_data = pd.read_pickle('/container/home/millenium/Storage/Daniel/github/kaggle_competitions/M5_Forecasting_Accuracy/data/full_data.pkl')
m5_data = m5_data[m5_data.d <= 1913]

In [4]:
m5_data

id        item_id    dept_id   cat_id  \
0         HOBBIES_1_008_CA_1_validation  HOBBIES_1_008  HOBBIES_1  HOBBIES   
1         HOBBIES_1_009_CA_1_validation  HOBBIES_1_009  HOBBIES_1  HOBBIES   
2         HOBBIES_1_010_CA_1_validation  HOBBIES_1_010  HOBBIES_1  HOBBIES   
3         HOBBIES_1_012_CA_1_validation  HOBBIES_1_012  HOBBIES_1  HOBBIES   
4         HOBBIES_1_015_CA_1_validation  HOBBIES_1_015  HOBBIES_1  HOBBIES   
...                                 ...            ...        ...      ...   
46027952    FOODS_3_823_WI_3_validation    FOODS_3_823    FOODS_3    FOODS   
46027953    FOODS_3_824_WI_3_validation    FOODS_3_824    FOODS_3    FOODS   
46027954    FOODS_3_825_WI_3_validation    FOODS_3_825    FOODS_3    FOODS   
46027955    FOODS_3_826_WI_3_validation    FOODS_3_826    FOODS_3    FOODS   
46027956    FOODS_3_827_WI_3_validation    FOODS_3_827    FOODS_3    FOODS   

         store_id state_id     d  sales  release  sell_price  ...  snap_CA  \
0            CA_1       CA     1   12.0        0    0.459961  ...        0   
1            CA_1       CA     1    2.0        0    1.559570  ...        0   
2            CA_1       CA     1    0.0        0    3.169922  ...        0   
3            CA_1       CA     1    0.0        0    5.980469  ...        0   
4            CA_1       CA     1    4.0        0    0.700195  ...        0   
...           ...      ...   ...    ...      ...         ...  ...      ...   
46027952     WI_3       WI  1913    1.0        0    2.980469  ...        0   
46027953     WI_3       WI  1913    0.0        0    2.480469  ...        0   
46027954     WI_3       WI  1913    0.0        0    3.980469  ...        0   
46027955     WI_3       WI  1913    3.0      230    1.280273  ...        0   
46027956     WI_3       WI  1913    0.0      304    1.000000  ...        0   

          snap_TX  snap_WI  tm_d  tm_w  tm_m  tm_y  tm_wm  tm_dw  tm_w_end  
0               0        0    29     4     1     0      5      5         1  
1               0        0    29     4     1     0      5      5         1  
2               0        0    29     4     1     0      5      5         1  
3               0        0    29     4     1     0      5      5         1  
4               0        0    29     4     1     0      5      5         1  
...           ...      ...   ...   ...   ...   ...    ...    ...       ...  
46027952        0        0    24    16     4     5      4      6         1  
46027953        0        0    24    16     4     5      4      6         1  
46027954        0        0    24    16     4     5      4      6         1  
46027955        0        0    24    16     4     5      4      6         1  
46027956        0        0    24    16     4     5      4      6         1  

[46027957 rows x 34 columns]

In [12]:
m5_data.index[:5]

Int64Index([0, 1, 2, 3, 4], dtype='int64')

In [13]:
m5_data.iloc[m5_data.index[:5]]

id        item_id    dept_id   cat_id store_id  \
0  HOBBIES_1_008_CA_1_validation  HOBBIES_1_008  HOBBIES_1  HOBBIES     CA_1   
1  HOBBIES_1_009_CA_1_validation  HOBBIES_1_009  HOBBIES_1  HOBBIES     CA_1   
2  HOBBIES_1_010_CA_1_validation  HOBBIES_1_010  HOBBIES_1  HOBBIES     CA_1   
3  HOBBIES_1_012_CA_1_validation  HOBBIES_1_012  HOBBIES_1  HOBBIES     CA_1   
4  HOBBIES_1_015_CA_1_validation  HOBBIES_1_015  HOBBIES_1  HOBBIES     CA_1   

  state_id  d  sales  release  sell_price  ...  snap_CA  snap_TX  snap_WI  \
0       CA  1   12.0        0    0.459961  ...        0        0        0   
1       CA  1    2.0        0    1.559570  ...        0        0        0   
2       CA  1    0.0        0    3.169922  ...        0        0        0   
3       CA  1    0.0        0    5.980469  ...        0        0        0   
4       CA  1    4.0        0    0.700195  ...        0        0        0   

   tm_d  tm_w  tm_m  tm_y  tm_wm  tm_dw  tm_w_end  
0    29     4     1     0      5      5         1  
1    29     4     1     0      5      5         1  
2    29     4     1     0      5      5         1  
3    29     4     1     0      5      5         1  
4    29     4     1     0      5      5         1  

[5 rows x 34 columns]

In [4]:
m5_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 46027957 entries, 0 to 46027956
Data columns (total 34 columns):
 #   Column            Dtype   
---  ------            -----   
 0   id                category
 1   item_id           category
 2   dept_id           category
 3   cat_id            category
 4   store_id          category
 5   state_id          category
 6   d                 int16   
 7   sales             float64 
 8   release           int16   
 9   sell_price        float16 
 10  price_max         float16 
 11  price_min         float16 
 12  price_std         float16 
 13  price_mean        float16 
 14  price_norm        float16 
 15  price_nunique     float16 
 16  item_nunique      int16   
 17  price_momentum    float16 
 18  price_momentum_m  float16 
 19  price_momentum_y  float16 
 20  event_name_1      category
 21  event_type_1      category
 22  event_name_2      category
 23  event_type_2      category
 24  snap_CA           category
 25  snap_TX         

### Converting pandas to cudf

In [3]:
m5_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 46027957 entries, 0 to 46027956
Data columns (total 34 columns):
id                  category
item_id             category
dept_id             category
cat_id              category
store_id            category
state_id            category
d                   int16
sales               float64
release             int16
sell_price          float16
price_max           float16
price_min           float16
price_std           float16
price_mean          float16
price_norm          float16
price_nunique       float16
item_nunique        int16
price_momentum      float16
price_momentum_m    float16
price_momentum_y    float16
event_name_1        category
event_type_1        category
event_name_2        category
event_type_2        category
snap_CA             category
snap_TX             category
snap_WI             category
tm_d                int8
tm_w                int8
tm_m                int8
tm_y                int8
tm_wm               in

In [4]:
float16_cols = m5_data.select_dtypes(include=['float16']).columns

In [5]:
for col in float16_cols:
    m5_data[col] = m5_data[col].astype('float32')

In [6]:
m5_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 46027957 entries, 0 to 46027956
Data columns (total 34 columns):
id                  category
item_id             category
dept_id             category
cat_id              category
store_id            category
state_id            category
d                   int16
sales               float64
release             int16
sell_price          float32
price_max           float32
price_min           float32
price_std           float32
price_mean          float32
price_norm          float32
price_nunique       float32
item_nunique        int16
price_momentum      float32
price_momentum_m    float32
price_momentum_y    float32
event_name_1        category
event_type_1        category
event_name_2        category
event_type_2        category
snap_CA             category
snap_TX             category
snap_WI             category
tm_d                int8
tm_w                int8
tm_m                int8
tm_y                int8
tm_wm               in

In [7]:
m5_data_c = cudf.from_pandas(m5_data)

### Modifying Nan values

In [4]:
events = ['event_name_2','event_type_2','event_name_1','event_type_1']

In [5]:
for col in events:
    m5_data[col] = m5_data[col].astype(str)
    m5_data.loc[m5_data[m5_data[col] == 'nan'].index, col] = 'none'
    m5_data[col] = m5_data[col].astype('category')

In [6]:
m5_data.isna().sum().to_frame().rename(columns = {0: 'count'}).sort_values(by=['count'], ascending = False)

count
id                    0
snap_TX               0
price_momentum_y      0
event_name_1          0
event_type_1          0
event_name_2          0
event_type_2          0
snap_CA               0
snap_WI               0
item_id               0
tm_d                  0
tm_w                  0
tm_m                  0
tm_y                  0
tm_wm                 0
tm_dw                 0
price_momentum_m      0
price_momentum        0
item_nunique          0
price_nunique         0
price_norm            0
price_mean            0
price_std             0
price_min             0
price_max             0
sell_price            0
release               0
sales                 0
d                     0
state_id              0
store_id              0
cat_id                0
dept_id               0
tm_w_end              0

### Converting df to dask

In [8]:
m5_data_d = dd.from_pandas(m5_data, npartitions = 128)

In [9]:
m5_data_d.info()

<class 'dask.dataframe.core.DataFrame'>
Columns: 34 entries, id to tm_w_end
dtypes: category(1), category(1), category(1), category(1), category(1), category(1), category(1), category(1), category(1), category(1), category(3), float16(10), float64(1), int16(3), int8(7)

### Column Definition

In [7]:
column_definitions = [
  ('id', DataTypes.CATEGORICAL, InputTypes.ID),
  ('sales', DataTypes.REAL_VALUED, InputTypes.TARGET),

  ('d', DataTypes.CATEGORICAL, InputTypes.TIME),
  ('event_name_2', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
  ('event_type_2', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
  ('event_name_1', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
  ('event_type_1', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
  ('snap_WI', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('snap_CA', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('snap_TX', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),

  ('price_momentum', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_momentum_m', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_momentum_y', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),

  ('price_max', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_min', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_std', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_mean', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_norm', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('price_nunique', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
  ('sell_price', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),

  ('tm_d', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('tm_w', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('tm_m', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('tm_y', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('tm_wm', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('tm_dw', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
  ('tm_w_end', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),

  ('snap_TX', DataTypes.REAL_VALUED, InputTypes.OBSERVED_INPUT),
  ('snap_CA', DataTypes.REAL_VALUED, InputTypes.OBSERVED_INPUT),
  ('snap_WI', DataTypes.REAL_VALUED, InputTypes.OBSERVED_INPUT),

  ('item_nunique', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
  ('release', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT), 
  ('item_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT), 
  ('dept_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
  ('cat_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
  ('store_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
  ('state_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
]

### Reviewing datasets

In [3]:
m5_data.shape

(46027957, 34)

In [4]:
m5_data.id.unique().shape

(30490,)

In [6]:
m5_data.isna().sum().to_frame().rename(columns = {0: 'count'}).sort_values(by=['count'], ascending = False)

count
event_name_2      45933474
event_type_2      45933474
event_name_1      42341567
event_type_1      42341567
id                       0
snap_TX                  0
price_momentum_y         0
snap_CA                  0
snap_WI                  0
item_id                  0
tm_d                     0
tm_w                     0
tm_m                     0
tm_y                     0
tm_wm                    0
tm_dw                    0
price_momentum_m         0
price_momentum           0
item_nunique             0
price_nunique            0
price_norm               0
price_mean               0
price_std                0
price_min                0
price_max                0
sell_price               0
release                  0
sales                    0
d                        0
state_id                 0
store_id                 0
cat_id                   0
dept_id                  0
tm_w_end                 0

In [8]:
valid_boundary=1913-(72*2 + 28)+1
test_boundary=1913-72+1

In [9]:
index = m5_data['d']
train = m5_data.loc[index < valid_boundary]
valid = m5_data.loc[(index >= valid_boundary) & (index < test_boundary)]
test = m5_data.loc[index >= test_boundary]

In [10]:
train.isna().sum().to_frame().rename(columns = {0: 'count'}).sort_values(by=['count'], ascending = False)

count
event_name_2      40691167
event_type_2      40691167
event_name_1      37556444
event_type_1      37556444
id                       0
snap_TX                  0
price_momentum_y         0
snap_CA                  0
snap_WI                  0
item_id                  0
tm_d                     0
tm_w                     0
tm_m                     0
tm_y                     0
tm_wm                    0
tm_dw                    0
price_momentum_m         0
price_momentum           0
item_nunique             0
price_nunique            0
price_norm               0
price_mean               0
price_std                0
price_min                0
price_max                0
sell_price               0
release                  0
sales                    0
d                        0
state_id                 0
store_id                 0
cat_id                   0
dept_id                  0
tm_w_end                 0

In [11]:
valid.isna().sum().to_frame().rename(columns = {0: 'count'}).sort_values(by=['count'], ascending = False)

count
event_name_2      3047027
event_type_2      3047027
event_name_1      2772783
event_type_1      2772783
id                      0
snap_TX                 0
price_momentum_y        0
snap_CA                 0
snap_WI                 0
item_id                 0
tm_d                    0
tm_w                    0
tm_m                    0
tm_y                    0
tm_wm                   0
tm_dw                   0
price_momentum_m        0
price_momentum          0
item_nunique            0
price_nunique           0
price_norm              0
price_mean              0
price_std               0
price_min               0
price_max               0
sell_price              0
release                 0
sales                   0
d                       0
state_id                0
store_id                0
cat_id                  0
dept_id                 0
tm_w_end                0

In [12]:
test.isna().sum().to_frame().rename(columns = {0: 'count'}).sort_values(by=['count'], ascending = False)

count
event_name_2      2195280
event_type_2      2195280
event_name_1      2012340
event_type_1      2012340
id                      0
snap_TX                 0
price_momentum_y        0
snap_CA                 0
snap_WI                 0
item_id                 0
tm_d                    0
tm_w                    0
tm_m                    0
tm_y                    0
tm_wm                   0
tm_dw                   0
price_momentum_m        0
price_momentum          0
item_nunique            0
price_nunique           0
price_norm              0
price_mean              0
price_std               0
price_min               0
price_max               0
sell_price              0
release                 0
sales                   0
d                       0
state_id                0
store_id                0
cat_id                  0
dept_id                 0
tm_w_end                0

### Testing Speeds

#### Faster Apply method

In [48]:
real_inputs = extract_cols_from_data_type(
            DataTypes.REAL_VALUED, column_definitions,
            {InputTypes.ID, InputTypes.TIME})

In [49]:
len(real_inputs)

14

In [50]:
id_column = 'id'
target_column = 'sales'
real_scalers = {}
target_scaler = {}
identifiers = []
time_steps = 72 + 28

In [51]:
def create_real_scalers(x):
    
    data = x[real_inputs].values
    targets = x[[target_column]].values
    
    real_scaler = StandardScaler().fit(data)
    target_scaler = StandardScaler().fit(targets)

    return real_scaler, target_scaler

Using Sklearn StandarScaler

In [52]:
trained_scalers = m5_data[[id_column] + 
                          real_inputs].groupby(id_column).apply(lambda x: pd.Series(create_real_scalers(x))) \
                  .rename(columns = {0:'real',
                                     1: 'target'})

In [53]:
trained_scalers

real  \
id                                                                                   
FOODS_1_001_CA_1_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_2_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_3_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_4_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_TX_1_validation      StandardScaler(copy=True, with_mean=True, with...   
...                                                                            ...   
HOUSEHOLD_2_516_TX_2_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_TX_3_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_1_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_2_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_3_validation  StandardScaler(copy=True, with_mean=True, with...   

                                                                            target  
id                                                                                  
FOODS_1_001_CA_1_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_2_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_3_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_4_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_TX_1_validation      StandardScaler(copy=True, with_mean=True, with...  
...                                                                            ...  
HOUSEHOLD_2_516_TX_2_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_TX_3_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_1_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_2_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_3_validation  StandardScaler(copy=True, with_mean=True, with...  

[30490 rows x 2 columns]

In [54]:
real_scalers = trained_scalers.real.to_dict()
target_scaler = trained_scalers.target.to_dict()
identifiers = trained_scalers.index.values

#### Slower For loop Method

In [64]:
real_inputs = extract_cols_from_data_type(
            DataTypes.REAL_VALUED, column_definitions,
            {InputTypes.ID, InputTypes.TIME})

In [65]:
id_column = 'id'
target_column = 'sales'
real_scalers = {}
target_scaler = {}
identifiers = []
time_steps = 72 + 28

In [66]:
for identifier, sliced in m5_data.groupby(id_column):
    print('{} - {}'.format(identifier, len(sliced)))
    if len(sliced) >= time_steps:

        data = sliced[real_inputs].values
        targets = sliced[[target_column]].values
        real_scalers[identifier] \
        = sklearn.preprocessing.StandardScaler().fit(data)

        target_scaler[identifier] \
        = sklearn.preprocessing.StandardScaler().fit(targets)
        identifiers.append(identifier)

FOODS_1_001_CA_1_validation - 1913
FOODS_1_001_CA_2_validation - 1913
FOODS_1_001_CA_3_validation - 1913
FOODS_1_001_CA_4_validation - 1913
FOODS_1_001_TX_1_validation - 1913
FOODS_1_001_TX_2_validation - 1913
FOODS_1_001_TX_3_validation - 1906
FOODS_1_001_WI_1_validation - 1913
FOODS_1_001_WI_2_validation - 1913
FOODS_1_001_WI_3_validation - 1913
FOODS_1_002_CA_1_validation - 1913
FOODS_1_002_CA_2_validation - 1913
FOODS_1_002_CA_3_validation - 1913
FOODS_1_002_CA_4_validation - 1913
FOODS_1_002_TX_1_validation - 1906
FOODS_1_002_TX_2_validation - 1913
FOODS_1_002_TX_3_validation - 1913
FOODS_1_002_WI_1_validation - 1913
FOODS_1_002_WI_2_validation - 1913
FOODS_1_002_WI_3_validation - 1913
FOODS_1_003_CA_1_validation - 1913
FOODS_1_003_CA_2_validation - 1913
FOODS_1_003_CA_3_validation - 1913
FOODS_1_003_CA_4_validation - 1913
FOODS_1_003_TX_1_validation - 1913
FOODS_1_003_TX_2_validation - 1913
FOODS_1_003_TX_3_validation - 1913
FOODS_1_003_WI_1_validation - 1913
FOODS_1_003_WI_2_val

FOODS_1_027_CA_4_validation - 1143
FOODS_1_027_TX_1_validation - 1276
FOODS_1_027_TX_2_validation - 1269
FOODS_1_027_TX_3_validation - 1276
FOODS_1_027_WI_1_validation - 1276
FOODS_1_027_WI_2_validation - 1276
FOODS_1_027_WI_3_validation - 1276
FOODS_1_028_CA_1_validation - 1101
FOODS_1_028_CA_2_validation - 1094
FOODS_1_028_CA_3_validation - 1101
FOODS_1_028_CA_4_validation - 1094
FOODS_1_028_TX_1_validation - 1094
FOODS_1_028_TX_2_validation - 1087
FOODS_1_028_TX_3_validation - 1087
FOODS_1_028_WI_1_validation - 1094
FOODS_1_028_WI_2_validation - 1101
FOODS_1_028_WI_3_validation - 1087
FOODS_1_029_CA_1_validation - 1850
FOODS_1_029_CA_2_validation - 1857
FOODS_1_029_CA_3_validation - 1843
FOODS_1_029_CA_4_validation - 408
FOODS_1_029_TX_1_validation - 1836
FOODS_1_029_TX_2_validation - 1850
FOODS_1_029_TX_3_validation - 1843
FOODS_1_029_WI_1_validation - 1843
FOODS_1_029_WI_2_validation - 1850
FOODS_1_029_WI_3_validation - 1850
FOODS_1_030_CA_1_validation - 1906
FOODS_1_030_CA_2_vali

FOODS_1_052_CA_1_validation - 1073
FOODS_1_052_CA_2_validation - 1073
FOODS_1_052_CA_3_validation - 1073
FOODS_1_052_CA_4_validation - 1073
FOODS_1_052_TX_1_validation - 1388
FOODS_1_052_TX_2_validation - 1381
FOODS_1_052_TX_3_validation - 1395
FOODS_1_052_WI_1_validation - 1388
FOODS_1_052_WI_2_validation - 1395
FOODS_1_052_WI_3_validation - 1381
FOODS_1_053_CA_1_validation - 1913
FOODS_1_053_CA_2_validation - 1913
FOODS_1_053_CA_3_validation - 1759
FOODS_1_053_CA_4_validation - 1913
FOODS_1_053_TX_1_validation - 1913
FOODS_1_053_TX_2_validation - 1913
FOODS_1_053_TX_3_validation - 1913
FOODS_1_053_WI_1_validation - 1913
FOODS_1_053_WI_2_validation - 1913
FOODS_1_053_WI_3_validation - 1878
FOODS_1_054_CA_1_validation - 1913
FOODS_1_054_CA_2_validation - 1913
FOODS_1_054_CA_3_validation - 1913
FOODS_1_054_CA_4_validation - 1836
FOODS_1_054_TX_1_validation - 1913
FOODS_1_054_TX_2_validation - 1913
FOODS_1_054_TX_3_validation - 1913
FOODS_1_054_WI_1_validation - 1892
FOODS_1_054_WI_2_val

FOODS_1_077_WI_3_validation - 1465
FOODS_1_078_CA_1_validation - 1164
FOODS_1_078_CA_2_validation - 1157
FOODS_1_078_CA_3_validation - 1164
FOODS_1_078_CA_4_validation - 1108
FOODS_1_078_TX_1_validation - 1150
FOODS_1_078_TX_2_validation - 1164
FOODS_1_078_TX_3_validation - 1150
FOODS_1_078_WI_1_validation - 1164
FOODS_1_078_WI_2_validation - 1157
FOODS_1_078_WI_3_validation - 1143
FOODS_1_079_CA_1_validation - 1584
FOODS_1_079_CA_2_validation - 1591
FOODS_1_079_CA_3_validation - 1591
FOODS_1_079_CA_4_validation - 1598
FOODS_1_079_TX_1_validation - 863
FOODS_1_079_TX_2_validation - 1913
FOODS_1_079_TX_3_validation - 877
FOODS_1_079_WI_1_validation - 1829
FOODS_1_079_WI_2_validation - 1871
FOODS_1_079_WI_3_validation - 1899
FOODS_1_080_CA_1_validation - 1913
FOODS_1_080_CA_2_validation - 1850
FOODS_1_080_CA_3_validation - 1913
FOODS_1_080_CA_4_validation - 1857
FOODS_1_080_TX_1_validation - 1913
FOODS_1_080_TX_2_validation - 1843
FOODS_1_080_TX_3_validation - 1913
FOODS_1_080_WI_1_valid

FOODS_1_103_WI_2_validation - 1899
FOODS_1_103_WI_3_validation - 1913
FOODS_1_104_CA_1_validation - 1913
FOODS_1_104_CA_2_validation - 1913
FOODS_1_104_CA_3_validation - 1913
FOODS_1_104_CA_4_validation - 1913
FOODS_1_104_TX_1_validation - 1913
FOODS_1_104_TX_2_validation - 1913
FOODS_1_104_TX_3_validation - 1913
FOODS_1_104_WI_1_validation - 1913
FOODS_1_104_WI_2_validation - 1913
FOODS_1_104_WI_3_validation - 1913
FOODS_1_105_CA_1_validation - 1591
FOODS_1_105_CA_2_validation - 1465
FOODS_1_105_CA_3_validation - 1591
FOODS_1_105_CA_4_validation - 1458
FOODS_1_105_TX_1_validation - 1507
FOODS_1_105_TX_2_validation - 1570
FOODS_1_105_TX_3_validation - 1507
FOODS_1_105_WI_1_validation - 1360
FOODS_1_105_WI_2_validation - 1402
FOODS_1_105_WI_3_validation - 1591
FOODS_1_106_CA_1_validation - 1913
FOODS_1_106_CA_2_validation - 1913
FOODS_1_106_CA_3_validation - 1913
FOODS_1_106_CA_4_validation - 1913
FOODS_1_106_TX_1_validation - 1913
FOODS_1_106_TX_2_validation - 1913
FOODS_1_106_TX_3_val

...

HOUSEHOLD_2_412_WI_2_validation - 1913
HOUSEHOLD_2_412_WI_3_validation - 1906
HOUSEHOLD_2_413_CA_1_validation - 632
HOUSEHOLD_2_413_CA_2_validation - 625
HOUSEHOLD_2_413_CA_3_validation - 632
HOUSEHOLD_2_413_CA_4_validation - 632
HOUSEHOLD_2_413_TX_1_validation - 625
HOUSEHOLD_2_413_TX_2_validation - 632
HOUSEHOLD_2_413_TX_3_validation - 632
HOUSEHOLD_2_413_WI_1_validation - 632
HOUSEHOLD_2_413_WI_2_validation - 632
HOUSEHOLD_2_413_WI_3_validation - 632
HOUSEHOLD_2_414_CA_1_validation - 1094
HOUSEHOLD_2_414_CA_2_validation - 702
HOUSEHOLD_2_414_CA_3_validation - 1087
HOUSEHOLD_2_414_CA_4_validation - 576
HOUSEHOLD_2_414_TX_1_validation - 695
HOUSEHOLD_2_414_TX_2_validation - 1073
HOUSEHOLD_2_414_TX_3_validation - 1080
HOUSEHOLD_2_414_WI_1_validation - 1094
HOUSEHOLD_2_414_WI_2_validation - 1080
HOUSEHOLD_2_414_WI_3_validation - 485
HOUSEHOLD_2_415_CA_1_validation - 1857
HOUSEHOLD_2_415_CA_2_validation - 1850
HOUSEHOLD_2_415_CA_3_validation - 1829
HOUSEHOLD_2_415_CA_4_validation - 1857


HOUSEHOLD_2_437_CA_4_validation - 1913
HOUSEHOLD_2_437_TX_1_validation - 1913
HOUSEHOLD_2_437_TX_2_validation - 1913
HOUSEHOLD_2_437_TX_3_validation - 1913
HOUSEHOLD_2_437_WI_1_validation - 1913
HOUSEHOLD_2_437_WI_2_validation - 1913
HOUSEHOLD_2_437_WI_3_validation - 1913
HOUSEHOLD_2_438_CA_1_validation - 1913
HOUSEHOLD_2_438_CA_2_validation - 1913
HOUSEHOLD_2_438_CA_3_validation - 1913
HOUSEHOLD_2_438_CA_4_validation - 1346
HOUSEHOLD_2_438_TX_1_validation - 1913
HOUSEHOLD_2_438_TX_2_validation - 1913
HOUSEHOLD_2_438_TX_3_validation - 1913
HOUSEHOLD_2_438_WI_1_validation - 1899
HOUSEHOLD_2_438_WI_2_validation - 1913
HOUSEHOLD_2_438_WI_3_validation - 1913
HOUSEHOLD_2_439_CA_1_validation - 1913
HOUSEHOLD_2_439_CA_2_validation - 1913
HOUSEHOLD_2_439_CA_3_validation - 1913
HOUSEHOLD_2_439_CA_4_validation - 1892
HOUSEHOLD_2_439_TX_1_validation - 1899
HOUSEHOLD_2_439_TX_2_validation - 1913
HOUSEHOLD_2_439_TX_3_validation - 1913
HOUSEHOLD_2_439_WI_1_validation - 1913
HOUSEHOLD_2_439_WI_2_vali

HOUSEHOLD_2_460_WI_2_validation - 1458
HOUSEHOLD_2_460_WI_3_validation - 1661
HOUSEHOLD_2_461_CA_1_validation - 1913
HOUSEHOLD_2_461_CA_2_validation - 1913
HOUSEHOLD_2_461_CA_3_validation - 1906
HOUSEHOLD_2_461_CA_4_validation - 1899
HOUSEHOLD_2_461_TX_1_validation - 1913
HOUSEHOLD_2_461_TX_2_validation - 1906
HOUSEHOLD_2_461_TX_3_validation - 1906
HOUSEHOLD_2_461_WI_1_validation - 1913
HOUSEHOLD_2_461_WI_2_validation - 1913
HOUSEHOLD_2_461_WI_3_validation - 1913
HOUSEHOLD_2_462_CA_1_validation - 1913
HOUSEHOLD_2_462_CA_2_validation - 1906
HOUSEHOLD_2_462_CA_3_validation - 1913
HOUSEHOLD_2_462_CA_4_validation - 1913
HOUSEHOLD_2_462_TX_1_validation - 1913
HOUSEHOLD_2_462_TX_2_validation - 1906
HOUSEHOLD_2_462_TX_3_validation - 1913
HOUSEHOLD_2_462_WI_1_validation - 1913
HOUSEHOLD_2_462_WI_2_validation - 1913
HOUSEHOLD_2_462_WI_3_validation - 1913
HOUSEHOLD_2_463_CA_1_validation - 611
HOUSEHOLD_2_463_CA_2_validation - 597
HOUSEHOLD_2_463_CA_3_validation - 618
HOUSEHOLD_2_463_CA_4_validat

HOUSEHOLD_2_485_CA_4_validation - 1661
HOUSEHOLD_2_485_TX_1_validation - 1913
HOUSEHOLD_2_485_TX_2_validation - 1906
HOUSEHOLD_2_485_TX_3_validation - 1913
HOUSEHOLD_2_485_WI_1_validation - 1913
HOUSEHOLD_2_485_WI_2_validation - 1913
HOUSEHOLD_2_485_WI_3_validation - 1885
HOUSEHOLD_2_486_CA_1_validation - 1906
HOUSEHOLD_2_486_CA_2_validation - 1913
HOUSEHOLD_2_486_CA_3_validation - 1913
HOUSEHOLD_2_486_CA_4_validation - 1913
HOUSEHOLD_2_486_TX_1_validation - 1913
HOUSEHOLD_2_486_TX_2_validation - 1913
HOUSEHOLD_2_486_TX_3_validation - 1913
HOUSEHOLD_2_486_WI_1_validation - 1913
HOUSEHOLD_2_486_WI_2_validation - 1913
HOUSEHOLD_2_486_WI_3_validation - 1913
HOUSEHOLD_2_487_CA_1_validation - 863
HOUSEHOLD_2_487_CA_2_validation - 877
HOUSEHOLD_2_487_CA_3_validation - 877
HOUSEHOLD_2_487_CA_4_validation - 877
HOUSEHOLD_2_487_TX_1_validation - 877
HOUSEHOLD_2_487_TX_2_validation - 877
HOUSEHOLD_2_487_TX_3_validation - 877
HOUSEHOLD_2_487_WI_1_validation - 863
HOUSEHOLD_2_487_WI_2_validation -

HOUSEHOLD_2_509_WI_3_validation - 1913
HOUSEHOLD_2_510_CA_1_validation - 1836
HOUSEHOLD_2_510_CA_2_validation - 1836
HOUSEHOLD_2_510_CA_3_validation - 1843
HOUSEHOLD_2_510_CA_4_validation - 1255
HOUSEHOLD_2_510_TX_1_validation - 1843
HOUSEHOLD_2_510_TX_2_validation - 1843
HOUSEHOLD_2_510_TX_3_validation - 1836
HOUSEHOLD_2_510_WI_1_validation - 1836
HOUSEHOLD_2_510_WI_2_validation - 1836
HOUSEHOLD_2_510_WI_3_validation - 1822
HOUSEHOLD_2_511_CA_1_validation - 1913
HOUSEHOLD_2_511_CA_2_validation - 1913
HOUSEHOLD_2_511_CA_3_validation - 1913
HOUSEHOLD_2_511_CA_4_validation - 1913
HOUSEHOLD_2_511_TX_1_validation - 1913
HOUSEHOLD_2_511_TX_2_validation - 1913
HOUSEHOLD_2_511_TX_3_validation - 1913
HOUSEHOLD_2_511_WI_1_validation - 1913
HOUSEHOLD_2_511_WI_2_validation - 1906
HOUSEHOLD_2_511_WI_3_validation - 1913
HOUSEHOLD_2_512_CA_1_validation - 1913
HOUSEHOLD_2_512_CA_2_validation - 1913
HOUSEHOLD_2_512_CA_3_validation - 1913
HOUSEHOLD_2_512_CA_4_validation - 1885
HOUSEHOLD_2_512_TX_1_vali

#### Testing Modin

In [8]:
real_inputs = extract_cols_from_data_type(
            DataTypes.REAL_VALUED, column_definitions,
            {InputTypes.ID, InputTypes.TIME})

In [9]:
id_column = 'id'
target_column = 'sales'
real_scalers = {}
target_scaler = {}
identifiers = []
time_steps = 72 + 28

In [10]:
def process_group(x):
    print('{} - {}'.format(x.name, len(x)))
    if len(x) >= time_steps:
        data = x[real_inputs].values
        targets = x[[target_column]].values
        real_scalers[x.name] \
        = sklearn.preprocessing.StandardScaler().fit(data)

        target_scaler[x.name] \
        = sklearn.preprocessing.StandardScaler().fit(targets)
        
        identifiers.append(x.name)

In [13]:
m5_data.groupby(id_column).apply(process_group)

distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker


CancelledError: 

distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker
distributed.nanny - WARNING - Worker exceeded 95% memory budget. Restarting
distributed.nanny - WARNING - Restarting worker


#### Testing Dask with apply

##### Training Scalers

In [11]:
real_inputs = extract_cols_from_data_type(
            DataTypes.REAL_VALUED, column_definitions,
            {InputTypes.ID, InputTypes.TIME})

In [12]:
real_inputs

['sales',
 'price_momentum',
 'price_momentum_m',
 'price_momentum_y',
 'price_max',
 'price_min',
 'price_std',
 'price_mean',
 'price_norm',
 'price_nunique',
 'sell_price',
 'snap_TX',
 'snap_CA',
 'snap_WI']

In [13]:
id_column = 'id'
target_column = 'sales'
#real_scalers = {}
#target_scaler = {}
#identifiers = []
time_steps = 72 + 28

In [14]:
m5_data_d[id_column] = m5_data_d[id_column].cat.as_ordered()
m5_data_d = m5_data_d.set_index(id_column)

In [15]:
def create_real_scalers(x):
    
    data = x[real_inputs].values
    targets = x[[target_column]].values
    
    real_scaler = StandardScaler().fit(data)
    target_scaler = StandardScaler().fit(targets)

    return real_scaler, target_scaler

In [16]:
result = m5_data_d.groupby(id_column).apply(lambda x: pd.Series(create_real_scalers(x)),
                                                      meta=[(0, object),
                                                            (1, object)]).compute().rename(columns={0:'real',
                                                                                                    1:'target'})
result

real  \
id                                                                                   
FOODS_1_001_CA_1_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_2_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_3_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_4_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_TX_1_validation      StandardScaler(copy=True, with_mean=True, with...   
...                                                                            ...   
HOUSEHOLD_2_516_TX_2_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_TX_3_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_1_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_2_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_3_validation  StandardScaler(copy=True, with_mean=True, with...   

                                                                            target  
id                                                                                  
FOODS_1_001_CA_1_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_2_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_3_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_4_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_TX_1_validation      StandardScaler(copy=True, with_mean=True, with...  
...                                                                            ...  
HOUSEHOLD_2_516_TX_2_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_TX_3_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_1_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_2_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_3_validation  StandardScaler(copy=True, with_mean=True, with...  

[30490 rows x 2 columns]

In [17]:
real_scalers = result.real.to_dict()

In [18]:
target_scaler = result.target.to_dict()

In [19]:
identifiers = result.index.values

In [31]:
#result = m5_data_d.groupby(id_column).apply(process_group, meta=pd.Series(dtype=object, name='real')).compute()
result = m5_data_d.groupby(id_column).apply(process_group, meta=('real',object)).compute()

In [47]:
result

id
FOODS_1_001_CA_1_validation        (StandardScaler(copy=True, with_mean=True, wit...
FOODS_1_001_CA_2_validation        (StandardScaler(copy=True, with_mean=True, wit...
FOODS_1_001_CA_3_validation        (StandardScaler(copy=True, with_mean=True, wit...
FOODS_1_001_CA_4_validation        (StandardScaler(copy=True, with_mean=True, wit...
FOODS_1_001_TX_1_validation        (StandardScaler(copy=True, with_mean=True, wit...
                                                         ...                        
HOUSEHOLD_2_516_TX_2_validation    (StandardScaler(copy=True, with_mean=True, wit...
HOUSEHOLD_2_516_TX_3_validation    (StandardScaler(copy=True, with_mean=True, wit...
HOUSEHOLD_2_516_WI_1_validation    (StandardScaler(copy=True, with_mean=True, wit...
HOUSEHOLD_2_516_WI_2_validation    (StandardScaler(copy=True, with_mean=True, wit...
HOUSEHOLD_2_516_WI_3_validation    (StandardScaler(copy=True, with_mean=True, wit...
Name: real, Length: 30490, dtype: object

In [51]:
result.apply(lambda x:pd.Series(x))

0  \
id                                                                                   
FOODS_1_001_CA_1_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_2_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_3_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_CA_4_validation      StandardScaler(copy=True, with_mean=True, with...   
FOODS_1_001_TX_1_validation      StandardScaler(copy=True, with_mean=True, with...   
...                                                                            ...   
HOUSEHOLD_2_516_TX_2_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_TX_3_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_1_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_2_validation  StandardScaler(copy=True, with_mean=True, with...   
HOUSEHOLD_2_516_WI_3_validation  StandardScaler(copy=True, with_mean=True, with...   

                                                                                 1  
id                                                                                  
FOODS_1_001_CA_1_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_2_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_3_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_CA_4_validation      StandardScaler(copy=True, with_mean=True, with...  
FOODS_1_001_TX_1_validation      StandardScaler(copy=True, with_mean=True, with...  
...                                                                            ...  
HOUSEHOLD_2_516_TX_2_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_TX_3_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_1_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_2_validation  StandardScaler(copy=True, with_mean=True, with...  
HOUSEHOLD_2_516_WI_3_validation  StandardScaler(copy=True, with_mean=True, with...  

[30490 rows x 2 columns]

##### Transforming Scalers

In [64]:
# Transform real inputs per entity
df_list = []
print('Real Features Transform')
%time
for identifier, sliced in m5_data.groupby(id_column):
    print('{} - {}'.format(identifier, len(sliced)))
    # Filter out any trajectories that are too short
    #if len(sliced) >= self._time_steps:
    sliced_copy = sliced.copy()
    sliced_copy[real_inputs] = real_scalers[identifier].transform(
        sliced_copy[real_inputs].values)
    df_list.append(sliced_copy)

Real Features Transform
CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 5.96 µs
FOODS_1_001_CA_1_validation - 1913
FOODS_1_001_CA_2_validation - 1913
FOODS_1_001_CA_3_validation - 1913
FOODS_1_001_CA_4_validation - 1913
FOODS_1_001_TX_1_validation - 1913
FOODS_1_001_TX_2_validation - 1913
FOODS_1_001_TX_3_validation - 1906
FOODS_1_001_WI_1_validation - 1913
FOODS_1_001_WI_2_validation - 1913
FOODS_1_001_WI_3_validation - 1913
FOODS_1_002_CA_1_validation - 1913
FOODS_1_002_CA_2_validation - 1913
FOODS_1_002_CA_3_validation - 1913
FOODS_1_002_CA_4_validation - 1913
FOODS_1_002_TX_1_validation - 1906
FOODS_1_002_TX_2_validation - 1913
FOODS_1_002_TX_3_validation - 1913
FOODS_1_002_WI_1_validation - 1913
FOODS_1_002_WI_2_validation - 1913
FOODS_1_002_WI_3_validation - 1913
FOODS_1_003_CA_1_validation - 1913
FOODS_1_003_CA_2_validation - 1913
FOODS_1_003_CA_3_validation - 1913
FOODS_1_003_CA_4_validation - 1913
FOODS_1_003_TX_1_validation - 1913
FOODS_1_003_TX_2_validation - 1913
FO

FOODS_1_025_TX_2_validation - 1234
FOODS_1_025_TX_3_validation - 1227
FOODS_1_025_WI_1_validation - 1248
FOODS_1_025_WI_2_validation - 1185
FOODS_1_025_WI_3_validation - 1178
FOODS_1_026_CA_1_validation - 1843
FOODS_1_026_CA_2_validation - 1913
FOODS_1_026_CA_3_validation - 1913
FOODS_1_026_CA_4_validation - 1913
FOODS_1_026_TX_1_validation - 1913
FOODS_1_026_TX_2_validation - 1913
FOODS_1_026_TX_3_validation - 1913
FOODS_1_026_WI_1_validation - 1913
FOODS_1_026_WI_2_validation - 1913
FOODS_1_026_WI_3_validation - 1913
FOODS_1_027_CA_1_validation - 1276
FOODS_1_027_CA_2_validation - 1276
FOODS_1_027_CA_3_validation - 1276
FOODS_1_027_CA_4_validation - 1143
FOODS_1_027_TX_1_validation - 1276
FOODS_1_027_TX_2_validation - 1269
FOODS_1_027_TX_3_validation - 1276
FOODS_1_027_WI_1_validation - 1276
FOODS_1_027_WI_2_validation - 1276
FOODS_1_027_WI_3_validation - 1276
FOODS_1_028_CA_1_validation - 1101
FOODS_1_028_CA_2_validation - 1094
FOODS_1_028_CA_3_validation - 1101
FOODS_1_028_CA_4_val

FOODS_1_049_TX_3_validation - 1913
FOODS_1_049_WI_1_validation - 1906
FOODS_1_049_WI_2_validation - 1913
FOODS_1_049_WI_3_validation - 1913
FOODS_1_050_CA_1_validation - 1647
FOODS_1_050_CA_2_validation - 1647
FOODS_1_050_CA_3_validation - 1654
FOODS_1_050_CA_4_validation - 1430
FOODS_1_050_TX_1_validation - 1633
FOODS_1_050_TX_2_validation - 1626
FOODS_1_050_TX_3_validation - 1528
FOODS_1_050_WI_1_validation - 1640
FOODS_1_050_WI_2_validation - 1619
FOODS_1_050_WI_3_validation - 1626
FOODS_1_051_CA_1_validation - 1066
FOODS_1_051_CA_2_validation - 1136
FOODS_1_051_CA_3_validation - 1129
FOODS_1_051_CA_4_validation - 1136
FOODS_1_051_TX_1_validation - 1381
FOODS_1_051_TX_2_validation - 1388
FOODS_1_051_TX_3_validation - 1374
FOODS_1_051_WI_1_validation - 1388
FOODS_1_051_WI_2_validation - 1374
FOODS_1_051_WI_3_validation - 1381
FOODS_1_052_CA_1_validation - 1073
FOODS_1_052_CA_2_validation - 1073
FOODS_1_052_CA_3_validation - 1073
FOODS_1_052_CA_4_validation - 1073
FOODS_1_052_TX_1_val

FOODS_1_073_TX_2_validation - 1913
FOODS_1_073_TX_3_validation - 1913
FOODS_1_073_WI_1_validation - 1913
FOODS_1_073_WI_2_validation - 1913
FOODS_1_073_WI_3_validation - 1913
FOODS_1_074_CA_1_validation - 1913
FOODS_1_074_CA_2_validation - 1913
FOODS_1_074_CA_3_validation - 1913
FOODS_1_074_CA_4_validation - 1913
FOODS_1_074_TX_1_validation - 1913
FOODS_1_074_TX_2_validation - 1913
FOODS_1_074_TX_3_validation - 1913
FOODS_1_074_WI_1_validation - 1913
FOODS_1_074_WI_2_validation - 1913
FOODS_1_074_WI_3_validation - 1913
FOODS_1_075_CA_1_validation - 1913
FOODS_1_075_CA_2_validation - 1913
FOODS_1_075_CA_3_validation - 1913
FOODS_1_075_CA_4_validation - 1913
FOODS_1_075_TX_1_validation - 1913
FOODS_1_075_TX_2_validation - 1913
FOODS_1_075_TX_3_validation - 1913
FOODS_1_075_WI_1_validation - 1913
FOODS_1_075_WI_2_validation - 1913
FOODS_1_075_WI_3_validation - 1892
FOODS_1_076_CA_1_validation - 1913
FOODS_1_076_CA_2_validation - 1913
FOODS_1_076_CA_3_validation - 1913
FOODS_1_076_CA_4_val

FOODS_1_098_TX_2_validation - 1255
FOODS_1_098_TX_3_validation - 1325
FOODS_1_098_WI_1_validation - 1318
FOODS_1_098_WI_2_validation - 1318
FOODS_1_098_WI_3_validation - 1318
FOODS_1_099_CA_1_validation - 1129
FOODS_1_099_CA_2_validation - 1129
FOODS_1_099_CA_3_validation - 1129
FOODS_1_099_CA_4_validation - 1129
FOODS_1_099_TX_1_validation - 1129
FOODS_1_099_TX_2_validation - 1129
FOODS_1_099_TX_3_validation - 1129
FOODS_1_099_WI_1_validation - 1129
FOODS_1_099_WI_2_validation - 1129
FOODS_1_099_WI_3_validation - 1122
FOODS_1_101_CA_1_validation - 1913
FOODS_1_101_CA_2_validation - 1913
FOODS_1_101_CA_3_validation - 1829
FOODS_1_101_CA_4_validation - 1913
FOODS_1_101_TX_1_validation - 1913
FOODS_1_101_TX_2_validation - 1906
FOODS_1_101_TX_3_validation - 1843
FOODS_1_101_WI_1_validation - 1913
FOODS_1_101_WI_2_validation - 1913
FOODS_1_101_WI_3_validation - 1913
FOODS_1_102_CA_1_validation - 1892
FOODS_1_102_CA_2_validation - 1857
FOODS_1_102_CA_3_validation - 1913
FOODS_1_102_CA_4_val

...

HOUSEHOLD_2_416_CA_1_validation - 1913
HOUSEHOLD_2_416_CA_2_validation - 1836
HOUSEHOLD_2_416_CA_3_validation - 1843
HOUSEHOLD_2_416_CA_4_validation - 1829
HOUSEHOLD_2_416_TX_1_validation - 1829
HOUSEHOLD_2_416_TX_2_validation - 1843
HOUSEHOLD_2_416_TX_3_validation - 1829
HOUSEHOLD_2_416_WI_1_validation - 1836
HOUSEHOLD_2_416_WI_2_validation - 1843
HOUSEHOLD_2_416_WI_3_validation - 1829
HOUSEHOLD_2_417_CA_1_validation - 1913
HOUSEHOLD_2_417_CA_2_validation - 1913
HOUSEHOLD_2_417_CA_3_validation - 1752
HOUSEHOLD_2_417_CA_4_validation - 1913
HOUSEHOLD_2_417_TX_1_validation - 1899
HOUSEHOLD_2_417_TX_2_validation - 1913
HOUSEHOLD_2_417_TX_3_validation - 1752
HOUSEHOLD_2_417_WI_1_validation - 1913
HOUSEHOLD_2_417_WI_2_validation - 1752
HOUSEHOLD_2_417_WI_3_validation - 1913
HOUSEHOLD_2_418_CA_1_validation - 485
HOUSEHOLD_2_418_CA_2_validation - 485
HOUSEHOLD_2_418_CA_3_validation - 485
HOUSEHOLD_2_418_CA_4_validation - 485
HOUSEHOLD_2_418_TX_1_validation - 478
HOUSEHOLD_2_418_TX_2_validatio

HOUSEHOLD_2_438_WI_1_validation - 1899
HOUSEHOLD_2_438_WI_2_validation - 1913
HOUSEHOLD_2_438_WI_3_validation - 1913
HOUSEHOLD_2_439_CA_1_validation - 1913
HOUSEHOLD_2_439_CA_2_validation - 1913
HOUSEHOLD_2_439_CA_3_validation - 1913
HOUSEHOLD_2_439_CA_4_validation - 1892
HOUSEHOLD_2_439_TX_1_validation - 1899
HOUSEHOLD_2_439_TX_2_validation - 1913
HOUSEHOLD_2_439_TX_3_validation - 1913
HOUSEHOLD_2_439_WI_1_validation - 1913
HOUSEHOLD_2_439_WI_2_validation - 1913
HOUSEHOLD_2_439_WI_3_validation - 1913
HOUSEHOLD_2_440_CA_1_validation - 1913
HOUSEHOLD_2_440_CA_2_validation - 1913
HOUSEHOLD_2_440_CA_3_validation - 1913
HOUSEHOLD_2_440_CA_4_validation - 1913
HOUSEHOLD_2_440_TX_1_validation - 1913
HOUSEHOLD_2_440_TX_2_validation - 1913
HOUSEHOLD_2_440_TX_3_validation - 1913
HOUSEHOLD_2_440_WI_1_validation - 1913
HOUSEHOLD_2_440_WI_2_validation - 1913
HOUSEHOLD_2_440_WI_3_validation - 1913
HOUSEHOLD_2_441_CA_1_validation - 1913
HOUSEHOLD_2_441_CA_2_validation - 1913
HOUSEHOLD_2_441_CA_3_vali

HOUSEHOLD_2_461_CA_2_validation - 1913
HOUSEHOLD_2_461_CA_3_validation - 1906
HOUSEHOLD_2_461_CA_4_validation - 1899
HOUSEHOLD_2_461_TX_1_validation - 1913
HOUSEHOLD_2_461_TX_2_validation - 1906
HOUSEHOLD_2_461_TX_3_validation - 1906
HOUSEHOLD_2_461_WI_1_validation - 1913
HOUSEHOLD_2_461_WI_2_validation - 1913
HOUSEHOLD_2_461_WI_3_validation - 1913
HOUSEHOLD_2_462_CA_1_validation - 1913
HOUSEHOLD_2_462_CA_2_validation - 1906
HOUSEHOLD_2_462_CA_3_validation - 1913
HOUSEHOLD_2_462_CA_4_validation - 1913
HOUSEHOLD_2_462_TX_1_validation - 1913
HOUSEHOLD_2_462_TX_2_validation - 1906
HOUSEHOLD_2_462_TX_3_validation - 1913
HOUSEHOLD_2_462_WI_1_validation - 1913
HOUSEHOLD_2_462_WI_2_validation - 1913
HOUSEHOLD_2_462_WI_3_validation - 1913
HOUSEHOLD_2_463_CA_1_validation - 611
HOUSEHOLD_2_463_CA_2_validation - 597
HOUSEHOLD_2_463_CA_3_validation - 618
HOUSEHOLD_2_463_CA_4_validation - 604
HOUSEHOLD_2_463_TX_1_validation - 604
HOUSEHOLD_2_463_TX_2_validation - 618
HOUSEHOLD_2_463_TX_3_validation

HOUSEHOLD_2_482_TX_1_validation - 1675
HOUSEHOLD_2_482_TX_2_validation - 1675
HOUSEHOLD_2_482_TX_3_validation - 1661
HOUSEHOLD_2_482_WI_1_validation - 1675
HOUSEHOLD_2_482_WI_2_validation - 1668
HOUSEHOLD_2_482_WI_3_validation - 1668
HOUSEHOLD_2_483_CA_1_validation - 1913
HOUSEHOLD_2_483_CA_2_validation - 1913
HOUSEHOLD_2_483_CA_3_validation - 1906
HOUSEHOLD_2_483_CA_4_validation - 1913
HOUSEHOLD_2_483_TX_1_validation - 1913
HOUSEHOLD_2_483_TX_2_validation - 1913
HOUSEHOLD_2_483_TX_3_validation - 1913
HOUSEHOLD_2_483_WI_1_validation - 1913
HOUSEHOLD_2_483_WI_2_validation - 1913
HOUSEHOLD_2_483_WI_3_validation - 1913
HOUSEHOLD_2_484_CA_1_validation - 1556
HOUSEHOLD_2_484_CA_2_validation - 1542
HOUSEHOLD_2_484_CA_3_validation - 1556
HOUSEHOLD_2_484_CA_4_validation - 1556
HOUSEHOLD_2_484_TX_1_validation - 1549
HOUSEHOLD_2_484_TX_2_validation - 1528
HOUSEHOLD_2_484_TX_3_validation - 1549
HOUSEHOLD_2_484_WI_1_validation - 1542
HOUSEHOLD_2_484_WI_2_validation - 1542
HOUSEHOLD_2_484_WI_3_vali

HOUSEHOLD_2_504_WI_1_validation - 1556
HOUSEHOLD_2_504_WI_2_validation - 1493
HOUSEHOLD_2_504_WI_3_validation - 1570
HOUSEHOLD_2_505_CA_1_validation - 1906
HOUSEHOLD_2_505_CA_2_validation - 1913
HOUSEHOLD_2_505_CA_3_validation - 1906
HOUSEHOLD_2_505_CA_4_validation - 1906
HOUSEHOLD_2_505_TX_1_validation - 1906
HOUSEHOLD_2_505_TX_2_validation - 1906
HOUSEHOLD_2_505_TX_3_validation - 1899
HOUSEHOLD_2_505_WI_1_validation - 1906
HOUSEHOLD_2_505_WI_2_validation - 1899
HOUSEHOLD_2_505_WI_3_validation - 1885
HOUSEHOLD_2_506_CA_1_validation - 1227
HOUSEHOLD_2_506_CA_2_validation - 1234
HOUSEHOLD_2_506_CA_3_validation - 1227
HOUSEHOLD_2_506_CA_4_validation - 1220
HOUSEHOLD_2_506_TX_1_validation - 1234
HOUSEHOLD_2_506_TX_2_validation - 1234
HOUSEHOLD_2_506_TX_3_validation - 1234
HOUSEHOLD_2_506_WI_1_validation - 1227
HOUSEHOLD_2_506_WI_2_validation - 1234
HOUSEHOLD_2_506_WI_3_validation - 1213
HOUSEHOLD_2_507_CA_1_validation - 1906
HOUSEHOLD_2_507_CA_2_validation - 1906
HOUSEHOLD_2_507_CA_3_vali

In [65]:
%time
output = pd.concat(df_list, axis=0)

CPU times: user 3 µs, sys: 1e+03 ns, total: 4 µs
Wall time: 7.63 µs


In [20]:
def transform_real_scalers(name_id, x):
    return real_scalers[name_id].transform(x[real_inputs].values)

In [25]:
len(real_inputs)

14

Using Normal Pandas

In [55]:
def transform_real_scalers(name, x):
    print(name)
    return pd.DataFrame(real_scalers[name].transform(x[real_inputs].values))

In [56]:
transform_real = m5_data[[id_column] + real_inputs].groupby(id_column).apply(lambda x: transform_real_scalers(x.name, x))
transform_real = transform_real.droplevel(level=None).reset_index()
transform_real.columns = [id_column] + real_inputs

FOODS_1_001_CA_1_validation
FOODS_1_001_CA_2_validation
FOODS_1_001_CA_3_validation
FOODS_1_001_CA_4_validation
FOODS_1_001_TX_1_validation
FOODS_1_001_TX_2_validation
FOODS_1_001_TX_3_validation
FOODS_1_001_WI_1_validation
FOODS_1_001_WI_2_validation
FOODS_1_001_WI_3_validation
FOODS_1_002_CA_1_validation
FOODS_1_002_CA_2_validation
FOODS_1_002_CA_3_validation
FOODS_1_002_CA_4_validation
FOODS_1_002_TX_1_validation
FOODS_1_002_TX_2_validation
FOODS_1_002_TX_3_validation
FOODS_1_002_WI_1_validation
FOODS_1_002_WI_2_validation
FOODS_1_002_WI_3_validation
FOODS_1_003_CA_1_validation
FOODS_1_003_CA_2_validation
FOODS_1_003_CA_3_validation
FOODS_1_003_CA_4_validation
FOODS_1_003_TX_1_validation
FOODS_1_003_TX_2_validation
FOODS_1_003_TX_3_validation
FOODS_1_003_WI_1_validation
FOODS_1_003_WI_2_validation
FOODS_1_003_WI_3_validation
FOODS_1_004_CA_1_validation
FOODS_1_004_CA_2_validation
FOODS_1_004_CA_3_validation
FOODS_1_004_CA_4_validation
FOODS_1_004_TX_1_validation
FOODS_1_004_TX_2_val

FOODS_1_032_WI_3_validation
FOODS_1_033_CA_1_validation
FOODS_1_033_CA_2_validation
FOODS_1_033_CA_3_validation
FOODS_1_033_CA_4_validation
FOODS_1_033_TX_1_validation
FOODS_1_033_TX_2_validation
FOODS_1_033_TX_3_validation
FOODS_1_033_WI_1_validation
FOODS_1_033_WI_2_validation
FOODS_1_033_WI_3_validation
FOODS_1_034_CA_1_validation
FOODS_1_034_CA_2_validation
FOODS_1_034_CA_3_validation
FOODS_1_034_CA_4_validation
FOODS_1_034_TX_1_validation
FOODS_1_034_TX_2_validation
FOODS_1_034_TX_3_validation
FOODS_1_034_WI_1_validation
FOODS_1_034_WI_2_validation
FOODS_1_034_WI_3_validation
FOODS_1_035_CA_1_validation
FOODS_1_035_CA_2_validation
FOODS_1_035_CA_3_validation
FOODS_1_035_CA_4_validation
FOODS_1_035_TX_1_validation
FOODS_1_035_TX_2_validation
FOODS_1_035_TX_3_validation
FOODS_1_035_WI_1_validation
FOODS_1_035_WI_2_validation
FOODS_1_035_WI_3_validation
FOODS_1_036_CA_1_validation
FOODS_1_036_CA_2_validation
FOODS_1_036_CA_3_validation
FOODS_1_036_CA_4_validation
FOODS_1_036_TX_1_val

FOODS_1_063_CA_1_validation
FOODS_1_063_CA_2_validation
FOODS_1_063_CA_3_validation
FOODS_1_063_CA_4_validation
FOODS_1_063_TX_1_validation
FOODS_1_063_TX_2_validation
FOODS_1_063_TX_3_validation
FOODS_1_063_WI_1_validation
FOODS_1_063_WI_2_validation
FOODS_1_063_WI_3_validation
FOODS_1_064_CA_1_validation
FOODS_1_064_CA_2_validation
FOODS_1_064_CA_3_validation
FOODS_1_064_CA_4_validation
FOODS_1_064_TX_1_validation
FOODS_1_064_TX_2_validation
FOODS_1_064_TX_3_validation
FOODS_1_064_WI_1_validation
FOODS_1_064_WI_2_validation
FOODS_1_064_WI_3_validation
FOODS_1_065_CA_1_validation
FOODS_1_065_CA_2_validation
FOODS_1_065_CA_3_validation
FOODS_1_065_CA_4_validation
FOODS_1_065_TX_1_validation
FOODS_1_065_TX_2_validation
FOODS_1_065_TX_3_validation
FOODS_1_065_WI_1_validation
FOODS_1_065_WI_2_validation
FOODS_1_065_WI_3_validation
FOODS_1_066_CA_1_validation
FOODS_1_066_CA_2_validation
FOODS_1_066_CA_3_validation
FOODS_1_066_CA_4_validation
FOODS_1_066_TX_1_validation
FOODS_1_066_TX_2_val

FOODS_1_092_WI_3_validation
FOODS_1_093_CA_1_validation
FOODS_1_093_CA_2_validation
FOODS_1_093_CA_3_validation
FOODS_1_093_CA_4_validation
FOODS_1_093_TX_1_validation
FOODS_1_093_TX_2_validation
FOODS_1_093_TX_3_validation
FOODS_1_093_WI_1_validation
FOODS_1_093_WI_2_validation
FOODS_1_093_WI_3_validation
FOODS_1_094_CA_1_validation
FOODS_1_094_CA_2_validation
FOODS_1_094_CA_3_validation
FOODS_1_094_CA_4_validation
FOODS_1_094_TX_1_validation
FOODS_1_094_TX_2_validation
FOODS_1_094_TX_3_validation
FOODS_1_094_WI_1_validation
FOODS_1_094_WI_2_validation
FOODS_1_094_WI_3_validation
FOODS_1_095_CA_1_validation
FOODS_1_095_CA_2_validation
FOODS_1_095_CA_3_validation
FOODS_1_095_CA_4_validation
FOODS_1_095_TX_1_validation
FOODS_1_095_TX_2_validation
FOODS_1_095_TX_3_validation
FOODS_1_095_WI_1_validation
FOODS_1_095_WI_2_validation
FOODS_1_095_WI_3_validation
FOODS_1_096_CA_1_validation
FOODS_1_096_CA_2_validation
FOODS_1_096_CA_3_validation
FOODS_1_096_CA_4_validation
FOODS_1_096_TX_1_val

FOODS_1_124_CA_1_validation
FOODS_1_124_CA_2_validation
FOODS_1_124_CA_3_validation
FOODS_1_124_CA_4_validation
FOODS_1_124_TX_1_validation
FOODS_1_124_TX_2_validation
FOODS_1_124_TX_3_validation
FOODS_1_124_WI_1_validation
FOODS_1_124_WI_2_validation
FOODS_1_124_WI_3_validation
FOODS_1_125_CA_1_validation
FOODS_1_125_CA_2_validation
FOODS_1_125_CA_3_validation
FOODS_1_125_CA_4_validation
FOODS_1_125_TX_1_validation
FOODS_1_125_TX_2_validation
FOODS_1_125_TX_3_validation
FOODS_1_125_WI_1_validation
FOODS_1_125_WI_2_validation
FOODS_1_125_WI_3_validation
FOODS_1_126_CA_1_validation
FOODS_1_126_CA_2_validation
FOODS_1_126_CA_3_validation
FOODS_1_126_CA_4_validation
FOODS_1_126_TX_1_validation
FOODS_1_126_TX_2_validation
FOODS_1_126_TX_3_validation
FOODS_1_126_WI_1_validation
FOODS_1_126_WI_2_validation
FOODS_1_126_WI_3_validation
FOODS_1_127_CA_1_validation
FOODS_1_127_CA_2_validation
FOODS_1_127_CA_3_validation
FOODS_1_127_CA_4_validation
FOODS_1_127_TX_1_validation
FOODS_1_127_TX_2_val

...

HOUSEHOLD_2_422_TX_2_validation
HOUSEHOLD_2_422_TX_3_validation
HOUSEHOLD_2_422_WI_1_validation
HOUSEHOLD_2_422_WI_2_validation
HOUSEHOLD_2_422_WI_3_validation
HOUSEHOLD_2_423_CA_1_validation
HOUSEHOLD_2_423_CA_2_validation
HOUSEHOLD_2_423_CA_3_validation
HOUSEHOLD_2_423_CA_4_validation
HOUSEHOLD_2_423_TX_1_validation
HOUSEHOLD_2_423_TX_2_validation
HOUSEHOLD_2_423_TX_3_validation
HOUSEHOLD_2_423_WI_1_validation
HOUSEHOLD_2_423_WI_2_validation
HOUSEHOLD_2_423_WI_3_validation
HOUSEHOLD_2_424_CA_1_validation
HOUSEHOLD_2_424_CA_2_validation
HOUSEHOLD_2_424_CA_3_validation
HOUSEHOLD_2_424_CA_4_validation
HOUSEHOLD_2_424_TX_1_validation
HOUSEHOLD_2_424_TX_2_validation
HOUSEHOLD_2_424_TX_3_validation
HOUSEHOLD_2_424_WI_1_validation
HOUSEHOLD_2_424_WI_2_validation
HOUSEHOLD_2_424_WI_3_validation
HOUSEHOLD_2_425_CA_1_validation
HOUSEHOLD_2_425_CA_2_validation
HOUSEHOLD_2_425_CA_3_validation
HOUSEHOLD_2_425_CA_4_validation
HOUSEHOLD_2_425_TX_1_validation
HOUSEHOLD_2_425_TX_2_validation
HOUSEHOL

HOUSEHOLD_2_450_WI_1_validation
HOUSEHOLD_2_450_WI_2_validation
HOUSEHOLD_2_450_WI_3_validation
HOUSEHOLD_2_451_CA_1_validation
HOUSEHOLD_2_451_CA_2_validation
HOUSEHOLD_2_451_CA_3_validation
HOUSEHOLD_2_451_CA_4_validation
HOUSEHOLD_2_451_TX_1_validation
HOUSEHOLD_2_451_TX_2_validation
HOUSEHOLD_2_451_TX_3_validation
HOUSEHOLD_2_451_WI_1_validation
HOUSEHOLD_2_451_WI_2_validation
HOUSEHOLD_2_451_WI_3_validation
HOUSEHOLD_2_452_CA_1_validation
HOUSEHOLD_2_452_CA_2_validation
HOUSEHOLD_2_452_CA_3_validation
HOUSEHOLD_2_452_CA_4_validation
HOUSEHOLD_2_452_TX_1_validation
HOUSEHOLD_2_452_TX_2_validation
HOUSEHOLD_2_452_TX_3_validation
HOUSEHOLD_2_452_WI_1_validation
HOUSEHOLD_2_452_WI_2_validation
HOUSEHOLD_2_452_WI_3_validation
HOUSEHOLD_2_453_CA_1_validation
HOUSEHOLD_2_453_CA_2_validation
HOUSEHOLD_2_453_CA_3_validation
HOUSEHOLD_2_453_CA_4_validation
HOUSEHOLD_2_453_TX_1_validation
HOUSEHOLD_2_453_TX_2_validation
HOUSEHOLD_2_453_TX_3_validation
HOUSEHOLD_2_453_WI_1_validation
HOUSEHOL

HOUSEHOLD_2_481_TX_1_validation
HOUSEHOLD_2_481_TX_2_validation
HOUSEHOLD_2_481_TX_3_validation
HOUSEHOLD_2_481_WI_1_validation
HOUSEHOLD_2_481_WI_2_validation
HOUSEHOLD_2_481_WI_3_validation
HOUSEHOLD_2_482_CA_1_validation
HOUSEHOLD_2_482_CA_2_validation
HOUSEHOLD_2_482_CA_3_validation
HOUSEHOLD_2_482_CA_4_validation
HOUSEHOLD_2_482_TX_1_validation
HOUSEHOLD_2_482_TX_2_validation
HOUSEHOLD_2_482_TX_3_validation
HOUSEHOLD_2_482_WI_1_validation
HOUSEHOLD_2_482_WI_2_validation
HOUSEHOLD_2_482_WI_3_validation
HOUSEHOLD_2_483_CA_1_validation
HOUSEHOLD_2_483_CA_2_validation
HOUSEHOLD_2_483_CA_3_validation
HOUSEHOLD_2_483_CA_4_validation
HOUSEHOLD_2_483_TX_1_validation
HOUSEHOLD_2_483_TX_2_validation
HOUSEHOLD_2_483_TX_3_validation
HOUSEHOLD_2_483_WI_1_validation
HOUSEHOLD_2_483_WI_2_validation
HOUSEHOLD_2_483_WI_3_validation
HOUSEHOLD_2_484_CA_1_validation
HOUSEHOLD_2_484_CA_2_validation
HOUSEHOLD_2_484_CA_3_validation
HOUSEHOLD_2_484_CA_4_validation
HOUSEHOLD_2_484_TX_1_validation
HOUSEHOL

HOUSEHOLD_2_511_TX_3_validation
HOUSEHOLD_2_511_WI_1_validation
HOUSEHOLD_2_511_WI_2_validation
HOUSEHOLD_2_511_WI_3_validation
HOUSEHOLD_2_512_CA_1_validation
HOUSEHOLD_2_512_CA_2_validation
HOUSEHOLD_2_512_CA_3_validation
HOUSEHOLD_2_512_CA_4_validation
HOUSEHOLD_2_512_TX_1_validation
HOUSEHOLD_2_512_TX_2_validation
HOUSEHOLD_2_512_TX_3_validation
HOUSEHOLD_2_512_WI_1_validation
HOUSEHOLD_2_512_WI_2_validation
HOUSEHOLD_2_512_WI_3_validation
HOUSEHOLD_2_513_CA_1_validation
HOUSEHOLD_2_513_CA_2_validation
HOUSEHOLD_2_513_CA_3_validation
HOUSEHOLD_2_513_CA_4_validation
HOUSEHOLD_2_513_TX_1_validation
HOUSEHOLD_2_513_TX_2_validation
HOUSEHOLD_2_513_TX_3_validation
HOUSEHOLD_2_513_WI_1_validation
HOUSEHOLD_2_513_WI_2_validation
HOUSEHOLD_2_513_WI_3_validation
HOUSEHOLD_2_514_CA_1_validation
HOUSEHOLD_2_514_CA_2_validation
HOUSEHOLD_2_514_CA_3_validation
HOUSEHOLD_2_514_CA_4_validation
HOUSEHOLD_2_514_TX_1_validation
HOUSEHOLD_2_514_TX_2_validation
HOUSEHOLD_2_514_TX_3_validation
HOUSEHOL

MemoryError: 

##### Tests

In [76]:
df = pd.DataFrame(data={'col1': list('aabccc'),
                        'col2': np.arange(6),
                        'col3': np.arange(6)})
df

col1  col2  col3
0    a     0     0
1    a     1     1
2    b     2     2
3    c     3     3
4    c     4     4
5    c     5     5

In [80]:
df.groupby(['col1']) \
.apply(lambda frame: frame \
       .transform(lambda col: col + 3 if frame.name == 'a' and col.name == 'col2' else col))

col1  col2  col3
0    a     3     0
1    a     4     1
2    b     2     2
3    c     3     3
4    c     4     4
5    c     5     5

In [106]:
df = pd.DataFrame({'A': range(3), 'B': range(1, 4)})
df

A  B
0  0  1
1  1  2
2  2  3

In [108]:
df.transform(lambda x: x + 1)

A  B
0  1  2
1  2  3
2  3  4

In [109]:
s = pd.Series(range(3))
s

0    0
1    1
2    2
dtype: int64

In [110]:
s.transform([np.sqrt, np.exp])

sqrt       exp
0  0.000000  1.000000
1  1.000000  2.718282
2  1.414214  7.389056

In [112]:
pd.DataFrame(np.random.rand(2,3))

0         1         2
0  0.720855  0.721911  0.651966
1  0.239244  0.570529  0.475872

##### Training Categorical

###### Original Implementation

In [13]:
# Format categorical scalers
categorical_inputs = extract_cols_from_data_type(
    DataTypes.CATEGORICAL, column_definitions,
    {InputTypes.ID, InputTypes.TIME})

In [14]:
categorical_inputs

['event_name_2',
 'event_type_2',
 'event_name_1',
 'event_type_1',
 'snap_WI',
 'snap_CA',
 'snap_TX',
 'tm_d',
 'tm_w',
 'tm_m',
 'tm_y',
 'tm_wm',
 'tm_dw',
 'tm_w_end',
 'item_nunique',
 'release',
 'item_id',
 'dept_id',
 'cat_id',
 'store_id',
 'state_id']

In [15]:
print('Categorical Scalers')
categorical_scalers = {}
num_classes = []
for col in categorical_inputs:
    srs = m5_data[col]
    if srs.dtype.name != 'category':
        # Set all to str so that we don't have mixed integer/string columns
        srs = srs.astype('category')
    categorical_scalers[col] = LabelEncoder().fit(srs.values)
    num_classes.append(srs.nunique())

Categorical Scalers


###### Optimizing with dask

In [25]:
def process_group(x):
    if x.dtype.name != 'category':
        x = x.astype('category') 
    
    label_encoder = LabelEncoder()
    
    return x.nunique(), label_encoder.fit(x.values)

Using only pandas

In [31]:
result = m5_data[categorical_inputs].apply(process_group)
result

event_name_2    event_type_2    event_name_1    event_type_1  \
0               5               3              31               5   
1  LabelEncoder()  LabelEncoder()  LabelEncoder()  LabelEncoder()   

          snap_WI         snap_CA         snap_TX            tm_d  \
0               2               2               2              31   
1  LabelEncoder()  LabelEncoder()  LabelEncoder()  LabelEncoder()   

             tm_w            tm_m  ...           tm_wm           tm_dw  \
0              53              12  ...               5               7   
1  LabelEncoder()  LabelEncoder()  ...  LabelEncoder()  LabelEncoder()   

         tm_w_end    item_nunique         release         item_id  \
0               2             184             259            3049   
1  LabelEncoder()  LabelEncoder()  LabelEncoder()  LabelEncoder()   

          dept_id          cat_id        store_id        state_id  
0               7               3              10               3  
1  LabelEncoder()  LabelEncoder()  LabelEncoder()  LabelEncoder()  

[2 rows x 21 columns]

In [34]:
process_group(m5_data[categorical_inputs])

AttributeError: 'DataFrame' object has no attribute 'dtype'

In [24]:
result.to_dict()['event_name_2']

LabelEncoder()

Using pandas with numba function speed

In [27]:
import numba

In [32]:
process_group_numba = numba.jit(process_group)

In [33]:
result = m5_data[categorical_inputs].apply(process_group_numba)
result

Compilation is falling back to object mode WITH looplifting enabled because Function "process_group" failed type inference due to: Untyped global name 'LabelEncoder': cannot determine Numba type of <class 'type'>

File "<ipython-input-31-2e82c76b9046>", line 5:
def process_group(x):
    <source elided>
    
    label_encoder = LabelEncoder()
    ^


File "<ipython-input-31-2e82c76b9046>", line 1:
def process_group(x):
^

Fall-back from the nopython compilation path to the object mode compilation path has been detected, this is deprecated behaviour.

For more information visit http://numba.pydata.org/numba-doc/latest/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit

File "<ipython-input-31-2e82c76b9046>", line 1:
def process_group(x):
^



event_name_2    LabelEncoder()
event_type_2    LabelEncoder()
event_name_1    LabelEncoder()
event_type_1    LabelEncoder()
snap_WI         LabelEncoder()
snap_CA         LabelEncoder()
snap_TX         LabelEncoder()
tm_d            LabelEncoder()
tm_w            LabelEncoder()
tm_m            LabelEncoder()
tm_y            LabelEncoder()
tm_wm           LabelEncoder()
tm_dw           LabelEncoder()
tm_w_end        LabelEncoder()
item_nunique    LabelEncoder()
release         LabelEncoder()
item_id         LabelEncoder()
dept_id         LabelEncoder()
cat_id          LabelEncoder()
store_id        LabelEncoder()
state_id        LabelEncoder()
dtype: object

Using dask with original implementation

In [10]:
m5_data_d['event_name_2'].compute().values

[none, none, none, none, none, ..., none, none, none, none, none]
Length: 46027957
Categories (5, object): [Cinco De Mayo, Easter, Father's day, OrthodoxEaster, none]

In [17]:
print('Categorical Scalers')
categorical_scalers = {}
num_classes = []
for col in categorical_inputs:
    srs = m5_data_d[col]
    if srs.dtype.name != 'category':
        # Set all to str so that we don't have mixed integer/string columns
        srs = srs.astype('category')
    categorical_scalers[col] = LabelEncoder().fit(srs.compute().values)
    num_classes.append(srs.nunique())

Categorical Scalers


In [23]:
result = m5_data_d[categorical_inputs].apply(process_group, axis = 1, meta = object).compute()
result

TypeError: argument must be a string or number

## Testing DataFormatter with only Pandas Optimization

In [8]:
class M5Formatter(GenericDataFormatter):
    """Defines and formats data for the electricity dataset.
    Note that per-entity z-score normalization is used here, and is implemented
    across functions.
    Attributes:
    column_definition: Defines input and data type of column used in the
      experiment.
    identifiers: Entity identifiers used in experiments.
    """

    _column_definition = [
      ('id', DataTypes.CATEGORICAL, InputTypes.ID),
      ('sales', DataTypes.REAL_VALUED, InputTypes.TARGET),
        
      ('d', DataTypes.CATEGORICAL, InputTypes.TIME),
      ('event_name_2', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
      ('event_type_2', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
      ('event_name_1', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
      ('event_type_1', DataTypes.CATEGORICAL, InputTypes.OBSERVED_INPUT),
      ('snap_WI', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('snap_CA', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('snap_TX', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
        
      ('price_momentum', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_momentum_m', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_momentum_y', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),

      ('price_max', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_min', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_std', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_mean', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_norm', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('price_nunique', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
      ('sell_price', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
        
      ('tm_d', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('tm_w', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('tm_m', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('tm_y', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('tm_wm', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('tm_dw', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
      ('tm_w_end', DataTypes.CATEGORICAL, InputTypes.KNOWN_INPUT),
        
      ('snap_TX', DataTypes.REAL_VALUED, InputTypes.OBSERVED_INPUT),
      ('snap_CA', DataTypes.REAL_VALUED, InputTypes.OBSERVED_INPUT),
      ('snap_WI', DataTypes.REAL_VALUED, InputTypes.OBSERVED_INPUT),
        
      ('item_nunique', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
      ('release', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT), 
      ('item_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT), 
      ('dept_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
      ('cat_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
      ('store_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
      ('state_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
    ]

    def __init__(self):
        """Initialises formatter."""

        self.identifiers = None
        self._real_scalers = None
        self._cat_scalers = None
        self._target_scaler = None
        self._num_classes_per_cat_input = None
        self._time_steps = self.get_fixed_params()['total_time_steps']
        self._num_encoder_steps = self.get_fixed_params()['num_encoder_steps']
        # Extract relevant columns
        self._column_definitions = self.get_column_definition()
        self._id_col = get_single_col_by_input_type(InputTypes.ID,
                                                    self._column_definitions)
        self._target_column = get_single_col_by_input_type(InputTypes.TARGET,
                                                           self._column_definitions)
        self._real_inputs = extract_cols_from_data_type(
                                                    DataTypes.REAL_VALUED, self._column_definitions,
                                                    {InputTypes.ID, InputTypes.TIME})
        self._categorical_inputs = extract_cols_from_data_type(
                                DataTypes.CATEGORICAL, self._column_definitions,
                                {InputTypes.ID, InputTypes.TIME})
        
    def get_time_steps(self):
        return self.get_fixed_params()['total_time_steps']
    
    def get_num_encoder_steps(self):
        return self.get_fixed_params()['num_encoder_steps']

    #def split_data(self, df, valid_boundary=1913-(72*2 + 28)+1, test_boundary=1913-72+1):
    def split_data(self, df, valid_boundary = 1913 - (28) + 1):
        """Splits data frame into training-validation-test data frames.
        This also calibrates scaling object, and transforms data for each split.
        Args:
          df: Source data frame to split.
          valid_boundary: Starting year for validation data
          test_boundary: Starting year for test data
        Returns:
          Tuple of transformed (train, valid, test) data.
        """

        print('Formatting train-valid-test splits.')

        index = df['d']
        train = df.loc[index < valid_boundary]
        valid = df.loc[(index >= valid_boundary)]
        #valid = df.loc[(index >= valid_boundary) & (index < test_boundary)]
        #test = df.loc[index >= test_boundary]

        self.set_scalers(train)
        
        return (self.transform_inputs(data_split) for data_split in [train, valid])#, test])
        #return (data.iloc[index_split] for index_split in [train_index, valid_index, test_index])
        #return data

    def set_scalers(self, df):
        """Calibrates scalers using the data supplied.
            Args:
              df: Data to use to calibrate scalers.
        """
        print('Setting scalers with all the data data...')
        print('Real Scalers')
        def create_real_scalers(x):

            data = x[self._real_inputs].values
            targets = x[[self._target_column]].values

            real_scaler = StandardScaler().fit(data)
            target_scaler = StandardScaler().fit(targets)

            return real_scaler, target_scaler
        
        scalers = df[[self._id_col] + 
                      self._real_inputs].groupby(self._id_col, observed = True) \
        .apply(lambda x: pd.Series(create_real_scalers(x))) \
        .rename(columns = {0:'real',
                           1: 'target'})

        self._real_scalers = scalers.real.to_dict()
        self._target_scaler = scalers.target.to_dict()
        # Extract identifiers in case required
        self.identifiers = scalers.index.values
        
        print('Categorical Scalers')
        categorical_scalers = {}
        num_classes = []
        for col in self._categorical_inputs:
            srs = df[col]
            if srs.dtype.name != 'category':
                # Set all to str so that we don't have mixed integer/string columns
                srs = srs.astype('category')
            categorical_scalers[col] = LabelEncoder().fit(
              srs.values)
            num_classes.append(srs.nunique())

        # Set categorical scaler outputs
        self._cat_scalers = categorical_scalers
        self._num_classes_per_cat_input = num_classes
        

    def transform_inputs(self, df):
        """Performs feature transformations.
        This includes both feature engineering, preprocessing and normalisation.
        Args:
          df: Data frame to transform.
        Returns:
          Transformed data frame.
        """
        print('Transforming all the data...')
        if self._real_scalers is None and self._cat_scalers is None:
            raise ValueError('Scalers have not been set!')
        
        print('Real Features Transform')
        output = df[[self._id_col] + 
                     self._real_inputs].groupby(self._id_col, observed = True) \
        .apply(lambda x: pd.DataFrame(self._real_scalers[x.name].transform(x[self._real_inputs].values)))
        output = output.droplevel(level=None).reset_index()
        output.columns = [self._id_col] + self._real_inputs 

        print('Categorical Features Transform')
        # Format categorical inputs
        for col in self._categorical_inputs:
            string_df = df[col]#.apply(str)
            output[col] = self._cat_scalers[col].transform(string_df)

        return output

    def format_predictions(self, predictions):
        """Reverts any normalisation to give predictions in original scale.
        Args:
          predictions: Dataframe of model predictions.
        Returns:
          Data frame of unnormalised predictions.
        """

        if self._target_scaler is None:
            raise ValueError('Scalers have not been set!')

        column_names = predictions.columns

        df_list = []
        for identifier, sliced in predictions.groupby('identifier'):
            sliced_copy = sliced.copy()
            target_scaler = self._target_scaler[identifier]

            for col in column_names:
                if col not in {'forecast_time', 'identifier'}:
                    sliced_copy[col] = target_scaler.inverse_transform(sliced_copy[col])
                    df_list.append(sliced_copy)

        output = pd.concat(df_list, axis=0)

        return output

    # Default params
    def get_fixed_params(self):
        """Returns fixed model parameters for experiments."""

        fixed_params = {
            'total_time_steps': 72,
            'num_encoder_steps': 72 - 28,
            'num_epochs': 100,
            'early_stopping_patience': 5,
            'multiprocessing_workers': 5
        }

        return fixed_params

    def get_default_model_params(self):
        """Returns default optimised model parameters."""

        model_params = {
            'dropout_rate': 0.1,
            'hidden_layer_size': 160,
            'learning_rate': 0.001,
            'minibatch_size': 64,
            'max_gradient_norm': 0.01,
            'num_heads': 4,
            'stack_size': 1
        }

        return model_params

    def get_num_samples_for_calibration(self):
        """Gets the default number of training and validation samples.
        Use to sub-sample the data for network calibration and a value of -1 uses
        all available samples.
        Returns:
          Tuple of (training samples, validation samples)
        """
        return 450000, 50000

## Formatting Data

In [ ]:
data_formatter = M5Formatter()
train, valid = data_formatter.split_data(m5_data)

Formatting train-valid-test splits.
Setting scalers with all the data data...
Real Scalers


In [ ]:
del m5_data

### Testing Split

In [23]:
train

id     sales  price_momentum  \
0           HOBBIES_1_008_CA_1_validation  0.525966       -0.017982   
1           HOBBIES_1_008_CA_1_validation  0.855788       -0.017982   
2           HOBBIES_1_008_CA_1_validation -0.793323       -0.017982   
3           HOBBIES_1_008_CA_1_validation -0.793323       -0.017982   
4           HOBBIES_1_008_CA_1_validation -0.793323       -0.017982   
...                                   ...       ...             ...   
45174232  HOUSEHOLD_1_020_WI_2_validation -0.987809        0.000000   
45174233  HOUSEHOLD_1_020_WI_2_validation -0.987809        0.000000   
45174234  HOUSEHOLD_1_020_WI_2_validation  0.186883        0.000000   
45174235  HOUSEHOLD_1_020_WI_2_validation  0.774229        0.000000   
45174236  HOUSEHOLD_1_020_WI_2_validation -0.987809        0.000000   

          price_momentum_m  price_momentum_y  price_max  price_min  price_std  \
0                -0.760401         -1.766613        0.0        0.0        0.0   
1                -0.760401         -1.766613        0.0        0.0        0.0   
2                -0.760401         -1.766613        0.0        0.0        0.0   
3                -0.760401         -1.766613        0.0        0.0        0.0   
4                -0.760401         -1.766613        0.0        0.0        0.0   
...                    ...               ...        ...        ...        ...   
45174232          0.000000          0.000000        0.0        0.0        0.0   
45174233          0.000000          0.000000        0.0        0.0        0.0   
45174234          0.000000          0.000000        0.0        0.0        0.0   
45174235          0.000000          0.000000        0.0        0.0        0.0   
45174236          0.000000          0.000000        0.0        0.0        0.0   

          price_mean  price_norm  ...  tm_wm  tm_dw  tm_w_end  item_nunique  \
0                0.0   -0.799985  ...      4      5         1            15   
1                0.0   -0.799985  ...      4      5         1             8   
2                0.0   -0.799985  ...      4      5         1            19   
3                0.0   -0.799985  ...      4      5         1            70   
4                0.0   -0.799985  ...      4      5         1            15   
...              ...         ...  ...    ...    ...       ...           ...   
45174232         0.0    0.000000  ...      3      6         1           164   
45174233         0.0    0.000000  ...      3      6         1           126   
45174234         0.0    0.000000  ...      3      6         1           137   
45174235         0.0    0.000000  ...      3      6         1            43   
45174236         0.0    0.000000  ...      3      6         1           131   

          release  item_id  dept_id  cat_id  store_id  state_id  
0               0     1444        3       1         0         0  
1               0     1445        3       1         0         0  
2               0     1446        3       1         0         0  
3               0     1448        3       1         0         0  
4               0     1451        3       1         0         0  
...           ...      ...      ...     ...       ...       ...  
45174232        0     1432        2       0         9         2  
45174233        0     1433        2       0         9         2  
45174234        0     1434        2       0         9         2  
45174235      134     1435        2       0         9         2  
45174236      161     1436        2       0         9         2  

[45174237 rows x 33 columns]

In [24]:
len(train['id'].unique()), len(valid['id'].unique())

(30490, 30490)

In [25]:
np.isin(valid.id.unique(),train.id.unique()).sum()

30490

### Doing Split by Hand

In [26]:
valid_boundary = 1913 - (28) + 1
valid_boundary

1886

In [29]:
len(m5_data.id.unique())

30490

In [30]:
index = m5_data['d']
index

0              1
1              1
2              1
3              1
4              1
            ... 
46027952    1913
46027953    1913
46027954    1913
46027955    1913
46027956    1913
Name: d, Length: 46027957, dtype: int16

In [31]:
train_index = m5_data.loc[index <= valid_boundary]
train_index

id        item_id    dept_id   cat_id  \
0         HOBBIES_1_008_CA_1_validation  HOBBIES_1_008  HOBBIES_1  HOBBIES   
1         HOBBIES_1_009_CA_1_validation  HOBBIES_1_009  HOBBIES_1  HOBBIES   
2         HOBBIES_1_010_CA_1_validation  HOBBIES_1_010  HOBBIES_1  HOBBIES   
3         HOBBIES_1_012_CA_1_validation  HOBBIES_1_012  HOBBIES_1  HOBBIES   
4         HOBBIES_1_015_CA_1_validation  HOBBIES_1_015  HOBBIES_1  HOBBIES   
...                                 ...            ...        ...      ...   
45204722    FOODS_3_823_WI_3_validation    FOODS_3_823    FOODS_3    FOODS   
45204723    FOODS_3_824_WI_3_validation    FOODS_3_824    FOODS_3    FOODS   
45204724    FOODS_3_825_WI_3_validation    FOODS_3_825    FOODS_3    FOODS   
45204725    FOODS_3_826_WI_3_validation    FOODS_3_826    FOODS_3    FOODS   
45204726    FOODS_3_827_WI_3_validation    FOODS_3_827    FOODS_3    FOODS   

         store_id state_id     d  sales  release  sell_price  ...  snap_CA  \
0            CA_1       CA     1   12.0        0    0.459961  ...        0   
1            CA_1       CA     1    2.0        0    1.559570  ...        0   
2            CA_1       CA     1    0.0        0    3.169922  ...        0   
3            CA_1       CA     1    0.0        0    5.980469  ...        0   
4            CA_1       CA     1    4.0        0    0.700195  ...        0   
...           ...      ...   ...    ...      ...         ...  ...      ...   
45204722     WI_3       WI  1886    0.0        0    2.980469  ...        0   
45204723     WI_3       WI  1886    0.0        0    2.000000  ...        0   
45204724     WI_3       WI  1886    1.0        0    3.980469  ...        0   
45204725     WI_3       WI  1886    3.0      230    1.280273  ...        0   
45204726     WI_3       WI  1886    7.0      304    1.000000  ...        0   

          snap_TX  snap_WI  tm_d  tm_w  tm_m  tm_y  tm_wm  tm_dw  tm_w_end  
0               0        0    29     4     1     0      5      5         1  
1               0        0    29     4     1     0      5      5         1  
2               0        0    29     4     1     0      5      5         1  
3               0        0    29     4     1     0      5      5         1  
4               0        0    29     4     1     0      5      5         1  
...           ...      ...   ...   ...   ...   ...    ...    ...       ...  
45204722        0        0    28    13     3     5      4      0         0  
45204723        0        0    28    13     3     5      4      0         0  
45204724        0        0    28    13     3     5      4      0         0  
45204725        0        0    28    13     3     5      4      0         0  
45204726        0        0    28    13     3     5      4      0         0  

[45204727 rows x 34 columns]

In [32]:
len(train_index.id.unique())

30490

In [33]:
train_index[train_index.id == 'FOODS_3_595_CA_1_validation']

id      item_id  dept_id cat_id store_id  \
43835496  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
43865986  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
43896476  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
43926966  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
43957456  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
43987946  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44018436  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44048926  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44079416  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44109906  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44140396  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44170886  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44201376  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44231866  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44262356  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44292846  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44323336  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44353826  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44384316  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44414806  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44445296  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44475786  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44506276  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44536766  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44567256  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44597746  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44628236  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44658726  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44689216  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44719706  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44750196  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44780686  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44811176  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44841666  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44872156  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44902646  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44933136  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44963626  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
44994116  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45024606  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45055096  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45085586  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45116076  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45146566  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45177056  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   

         state_id     d  sales  release  sell_price  ...  snap_CA  snap_TX  \
43835496       CA  1842    0.0      502    1.980469  ...        0        1   
43865986       CA  1843    0.0      502    1.980469  ...        0        0   
43896476       CA  1844    0.0      502    1.980469  ...        0        1   
43926966       CA  1845    0.0      502    1.980469  ...        0        0   
43957456  

In [34]:
valid_index = m5_data.loc[(index > valid_boundary)]# & (index < test_boundary)]
#test_index = m5_data.loc[index >= test_boundary]

In [35]:
valid_index[valid_index.id == 'FOODS_3_595_CA_1_validation']

id      item_id  dept_id cat_id store_id  \
45207546  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45238036  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45268526  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45299016  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45329506  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45359996  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45390486  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45420976  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45451466  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45481956  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45512446  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45542936  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45573426  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45603916  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45634406  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45664896  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45695386  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45725876  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45756366  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45786856  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45817346  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45847836  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45878326  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45908816  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45939306  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
45969796  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   
46000286  FOODS_3_595_CA_1_validation  FOODS_3_595  FOODS_3  FOODS     CA_1   

         state_id     d  sales  release  sell_price  ...  snap_CA  snap_TX  \
45207546       CA  1887    2.0      502    1.980469  ...        0        0   
45238036       CA  1888    2.0      502    1.980469  ...        0        0   
45268526       CA  1889    1.0      502    1.980469  ...        0        0   
45299016       CA  1890    2.0      502    1.980469  ...        1        1   
45329506       CA  1891    4.0      502    1.980469  ...        1        0   
45359996       CA  1892    0.0      502    1.980469  ...        1        1   
45390486       CA  1893    1.0      502    1.980469  ...        1        0   
45420976       CA  1894    1.0      502    1.980469  ...        1        1   
45451466       CA  1895    0.0      502    1.980469  ...        1        1   
45481956       CA  1896    1.0      502    1.980469  ...        1        1   
45512446       CA  1897    2.0      502    1.980469  ...        1        0   
45542936       CA  1898    4.0      502    1.980469  ...        1        1   
45573426       CA  1899    2.0      502    1.980469  ...        1        0   
45603916       CA  1900    1.0      502    1.980469  ...        0        1   
45634406       CA  1901    0.0      502    1.980469  ...        0        1   
45664896       CA  1902    3.0      502    1.980469  ...        0        1   
45695386       CA  1903    0.0      502    1.980469  ...        0        0   
45725876       CA  1904    1.0      502    1.980469  ...        0        1   
45756366       CA  1905    1.0      502    1.980469  ...        0        0   
45786856       CA  1906    1.0      502    1.980469  ...        0        0   
45817346       CA  1907    1.0      502    1.980469  ...        0        0   
45847836       CA  1908    2.0      502    1.980469  ...        0        0   
45878326       CA  1909    0

In [38]:
len(valid_index.id.unique())

30490

## Testing Pytorch Dataset

In [ ]:
class TFTDataset(Dataset, M5Formatter):
    """Dataset Basic Structure for Temporal Fusion Transformer"""

    def __init__(self, 
                 data_df):
        super(M5Formatter, self).__init__()
        """
        Args:
            csv_file (string): Path to the csv file with annotations.
        """
        # Attribute loading the data
        self.data = data_df.reset_index(drop=True)
        
        self.id_col = get_single_col_by_input_type(InputTypes.ID, self._column_definition)
        self.time_col = get_single_col_by_input_type(InputTypes.TIME, self._column_definition)
        self.target_col = get_single_col_by_input_type(InputTypes.TARGET, self._column_definition)
        self.input_cols = [
                            tup[0]
                            for tup in self._column_definition
                            if tup[2] not in {InputTypes.ID, InputTypes.TIME}
                          ]
        self.col_mappings = {
                              'identifier': [self.id_col],
                              'time': [self.time_col],
                              'outputs': [self.target_col],
                              'inputs': self.input_cols
                          }
        self.lookback = self.get_time_steps()
        self.num_encoder_steps = self.get_num_encoder_steps()
        
        self.data_index = self.get_index_filtering()
        self.group_size = self.data.groupby([self.id_col], observed = True).apply(lambda x: x.shape[0]).mean()
        self.data_index = self.data_index[self.data_index.end_rel < self.group_size].reset_index()
        
    def get_index_filtering(self):
        
        g = self.data.groupby([self.id_col])
        
        df_index_abs = g[[self.target_col]].transform(lambda x: x.index+self.lookback) \
                        .reset_index() \
                        .rename(columns={'index':'init_abs',
                                         self.target_col:'end_abs'})
        df_index_rel_init = g[[self.target_col]].transform(lambda x: x.reset_index(drop=True).index) \
                        .rename(columns={self.target_col:'init_rel'})
        df_index_rel_end = g[[self.target_col]].transform(lambda x: x.reset_index(drop=True).index+self.lookback) \
                        .rename(columns={self.target_col:'end_rel'})
        df_total_count = g[[self.target_col]].transform(lambda x: x.shape[0] - self.lookback + 1) \
                        .rename(columns = {self.target_col:'group_count'})
        
        return pd.concat([df_index_abs, 
                          df_index_rel_init,
                          df_index_rel_end,
                          self.data[[self.id_col]], 
                          df_total_count], axis = 1).reset_index(drop = True)

    def __len__(self):
        # In this case, the length of the dataset is not the length of the training data, 
        # rather the ammount of unique sequences in the data
        return self.data_index.shape[0]

    def __getitem__(self, idx):
        
        data_index = self.data.iloc[self.data_index.init_abs.iloc[idx]:self.data_index.end_abs.iloc[idx]]
        
        data_map = {}
        for k in self.col_mappings:
            cols = self.col_mappings[k]
            
            if k not in data_map:
                data_map[k] = [data_index[cols].values]
            else:
                data_map[k].append(data_index[cols].values)
                
        # Combine all data
        for k in data_map:
            data_map[k] = np.concatenate(data_map[k], axis=0)
        # Shorten target so we only get decoder steps
        data_map['outputs'] = data_map['outputs'][self.num_encoder_steps:, :]
        
        active_entries = np.ones_like(data_map['outputs'])
        if 'active_entries' not in data_map:
            data_map['active_entries'] = active_entries
        else:
            data_map['active_entries'].append(active_entries)
                
        return data_map['inputs'], data_map['outputs'], data_map['active_entries']

## Creation Datasets

In [ ]:
train_dataset = TFTDataset(train)

In [ ]:
valid_dataset = TFTDataset(valid)
#test_dataset = TFTDataset(test)

In [14]:
valid.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 853720 entries, 0 to 853719
Data columns (total 33 columns):
 #   Column            Non-Null Count   Dtype   
---  ------            --------------   -----   
 0   id                853720 non-null  category
 1   sales             853720 non-null  float64 
 2   price_momentum    853720 non-null  float64 
 3   price_momentum_m  853720 non-null  float64 
 4   price_momentum_y  853720 non-null  float64 
 5   price_max         853720 non-null  float64 
 6   price_min         853720 non-null  float64 
 7   price_std         853720 non-null  float64 
 8   price_mean        853720 non-null  float64 
 9   price_norm        853720 non-null  float64 
 10  price_nunique     853720 non-null  float64 
 11  sell_price        853720 non-null  float64 
 12  snap_TX           853720 non-null  int64   
 13  snap_CA           853720 non-null  int64   
 14  snap_WI           853720 non-null  int64   
 15  event_name_2      853720 non-null  int64   
 16  ev

In [13]:
valid_dataset[0]

IndexError: single positional indexer is out-of-bounds

## Temporal Fusion Transformer

In [ ]:
class TemporalFusionTransformer(pl.LightningModule):
    def __init__(self, hparams):
        super(TemporalFusionTransformer, self).__init__()
        
        self.hparams = hparams
        
        self.name = self.__class__.__name__

        # Data parameters
        self.time_steps = int(hparams.total_time_steps)#int(params['total_time_steps'])
        self.input_size = int(hparams.input_size)#int(params['input_size'])
        self.output_size = int(hparams.output_size)#int(params['output_size'])
        self.category_counts = json.loads(str(hparams.category_counts))#json.loads(str(params['category_counts']))
        self.num_categorical_variables = len(self.category_counts)
        self.num_regular_variables = self.input_size - self.num_categorical_variables
        self.n_multiprocessing_workers = int(hparams.multiprocessing_workers) #int(params['multiprocessing_workers'])

        # Relevant indices for TFT
        self._input_obs_loc = json.loads(str(hparams.input_obs_loc))#json.loads(str(params['input_obs_loc']))
        self._static_input_loc = json.loads(str(hparams.static_input_loc))#json.loads(str(params['static_input_loc']))
        self._known_regular_input_idx = json.loads(str(hparams.known_regular_inputs))#json.loads(str(params['known_regular_inputs']))
        self._known_categorical_input_idx = json.loads(str(hparams.known_categorical_inputs))#json.loads(str(params['known_categorical_inputs']))
        
        self.num_non_static_historical_inputs = self.get_historical_num_inputs()
        self.num_non_static_future_inputs = self.get_future_num_inputs()
        
        self.column_definition = [
                                  ('id', DataTypes.REAL_VALUED, InputTypes.ID),
                                  ('hours_from_start', DataTypes.REAL_VALUED, InputTypes.TIME),
                                  ('power_usage', DataTypes.REAL_VALUED, InputTypes.TARGET),
                                  ('hour', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
                                  ('day_of_week', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
                                  ('hours_from_start', DataTypes.REAL_VALUED, InputTypes.KNOWN_INPUT),
                                  ('categorical_id', DataTypes.CATEGORICAL, InputTypes.STATIC_INPUT),
                                ]

        # Network params
        self.quantiles = [0.1, 0.5, 0.9]
#         self.use_cudnn = use_cudnn  # Whether to use GPU optimised LSTM
        self.hidden_layer_size = int(hparams.hidden_layer_size)#int(params['hidden_layer_size'])
        self.dropout_rate = float(hparams.dropout_rate)#float(params['dropout_rate'])
        self.max_gradient_norm = float(hparams.max_gradient_norm)#float(params['max_gradient_norm'])
        self.learning_rate = float(hparams.learning_rate)#float(params['learning_rate'])
        self.minibatch_size = int(hparams.minibatch_size)#int(params['minibatch_size'])
        self.num_epochs = int(hparams.num_epochs)#int(params['num_epochs'])
        self.early_stopping_patience = int(hparams.early_stopping_patience)#int(params['early_stopping_patience'])

        self.num_encoder_steps = int(hparams.num_encoder_steps)#int(params['num_encoder_steps'])
        self.num_stacks = int(hparams.stack_size)#int(params['stack_size'])
        self.num_heads = int(hparams.num_heads)#int(params['num_heads'])

        # Serialisation options
#         self._temp_folder = os.path.join(params['model_folder'], 'tmp')
#         self.reset_temp_folder()

        # Extra components to store Tensorflow nodes for attention computations
        self._input_placeholder = None
        self._attention_components = None
        self._prediction_parts = None

        print('*** {} params ***'.format(self.name))
        for k in vars(hparams):
            print('# {} = {}'.format(k, vars(hparams)[k]))
            
        self.train_criterion = QuantileLossCalculator(self.quantiles, self.output_size)
        self.test_criterion = NormalizedQuantileLossCalculator(self.quantiles, self.output_size)

        # Build model
        ## Build embeddings
        self.build_embeddings()
        
        ## Build Static Contex Networks
        self.build_static_context_networks()
        
        ## Building Variable Selection Networks
        self.build_variable_selection_networks()
        
        ## Build Lstm
        self.build_lstm()
        
        ## Build GLU for after lstm encoder decoder and layernorm
        self.build_post_lstm_gate_add_norm()
        
        ## Build Static Enrichment Layer
        self.build_static_enrichment()
        
        ## Building decoder multihead attention
        self.build_temporal_self_attention()
        
        ## Building positionwise decoder
        self.build_position_wise_feed_forward()
        
        ## Build output feed forward
        self.build_output_feed_forward()
        
        ## Initializing remaining weights
        self.init_weights()
        
    def init_weights(self):
        for name, p in self.named_parameters():
            if ('lstm' in name and 'ih' in name) and 'bias' not in name:
                #print(name)
                #print(p.shape)
                torch.nn.init.xavier_uniform_(p)
#                 torch.nn.init.kaiming_normal_(p, a=0, mode='fan_in', nonlinearity='sigmoid')
            elif ('lstm' in name and 'hh' in name) and 'bias' not in name:
        
                 torch.nn.init.orthogonal_(p)
            
            elif 'lstm' in name and 'bias' in name:
                #print(name)
                #print(p.shape)
                torch.nn.init.zeros_(p)
        
    def get_historical_num_inputs(self):
        
        obs_inputs = [i for i in self._input_obs_loc]
        
        known_regular_inputs = [i for i in self._known_regular_input_idx
                                if i not in self._static_input_loc]
            
        known_categorical_inputs = [i for i in self._known_categorical_input_idx
                                    if i + self.num_regular_variables not in self._static_input_loc]
        
        wired_embeddings = [i for i in range(self.num_categorical_variables)
                            if i not in self._known_categorical_input_idx 
                            and i not in self._input_obs_loc]

        unknown_inputs = [i for i in range(self.num_regular_variables)
                          if i not in self._known_regular_input_idx
                          and i not in self._input_obs_loc]

        return len(obs_inputs+known_regular_inputs+known_categorical_inputs+wired_embeddings+unknown_inputs)
    
    def get_future_num_inputs(self):
            
        known_regular_inputs = [i for i in self._known_regular_input_idx
                                if i not in self._static_input_loc]
            
        known_categorical_inputs = [i for i in self._known_categorical_input_idx
                                    if i + self.num_regular_variables not in self._static_input_loc]

        return len(known_regular_inputs + known_categorical_inputs)
    
    def build_embeddings(self):
        self.categorical_var_embeddings = nn.ModuleList([nn.Embedding(self.category_counts[i], 
                                                                      self.hidden_layer_size) 
                                                     for i in range(self.num_categorical_variables)])

        self.regular_var_embeddings = nn.ModuleList([nn.Linear(1, 
                                                              self.hidden_layer_size) 
                                                  for i in range(self.num_regular_variables)])

    def build_variable_selection_networks(self):
        
        self.static_vsn = VariableSelectionNetwork(hidden_layer_size = self.hidden_layer_size,
                                                   input_size = self.hidden_layer_size * len(self._static_input_loc),
                                                   output_size = len(self._static_input_loc),
                                                   dropout_rate = self.dropout_rate)
        
        self.temporal_historical_vsn = VariableSelectionNetwork(hidden_layer_size = self.hidden_layer_size,
                                                                input_size = self.hidden_layer_size *
                                                                        self.num_non_static_historical_inputs,
                                                                output_size = self.num_non_static_historical_inputs,
                                                                dropout_rate = self.dropout_rate,
                                                                additional_context=self.hidden_layer_size)
        
        self.temporal_future_vsn = VariableSelectionNetwork(hidden_layer_size = self.hidden_layer_size,
                                                            input_size = self.hidden_layer_size *
                                                                        self.num_non_static_future_inputs,
                                                            output_size = self.num_non_static_future_inputs,
                                                            dropout_rate = self.dropout_rate,
                                                            additional_context=self.hidden_layer_size)
        
    def build_static_context_networks(self):
        
        self.static_context_variable_selection_grn = GatedResidualNetwork(self.hidden_layer_size,
                                                                          dropout_rate=self.dropout_rate)
        
        self.static_context_enrichment_grn = GatedResidualNetwork(self.hidden_layer_size,
                                                              dropout_rate=self.dropout_rate)

        self.static_context_state_h_grn = GatedResidualNetwork(self.hidden_layer_size,
                                                           dropout_rate=self.dropout_rate)
        
        self.static_context_state_c_grn = GatedResidualNetwork(self.hidden_layer_size,
                                                           dropout_rate=self.dropout_rate)
        
    def build_lstm(self):
        self.historical_lstm = nn.LSTM(input_size = self.hidden_layer_size,
                                       hidden_size = self.hidden_layer_size,
                                       batch_first = True)
        self.future_lstm = nn.LSTM(input_size = self.hidden_layer_size,
                                   hidden_size = self.hidden_layer_size,
                                   batch_first = True)
        
    def build_post_lstm_gate_add_norm(self):
        self.post_seq_encoder_gate_add_norm = GateAddNormNetwork(self.hidden_layer_size,
                                                                 self.hidden_layer_size,
                                                                 self.dropout_rate,
                                                                 activation = None)
        
    def build_static_enrichment(self):
        self.static_enrichment = GatedResidualNetwork(self.hidden_layer_size,
                                                      dropout_rate = self.dropout_rate,
                                                      additional_context=self.hidden_layer_size)
        
    def build_temporal_self_attention(self):
        self.self_attn_layer = InterpretableMultiHeadAttention(n_head = self.num_heads, 
                                                               d_model = self.hidden_layer_size,
                                                               dropout = self.dropout_rate)
        
        self.post_attn_gate_add_norm = GateAddNormNetwork(self.hidden_layer_size,
                                                           self.hidden_layer_size,
                                                           self.dropout_rate,
                                                           activation = None)
        
    def build_position_wise_feed_forward(self):
        self.GRN_positionwise = GatedResidualNetwork(self.hidden_layer_size,
                                                     dropout_rate = self.dropout_rate)
        
        self.post_tfd_gate_add_norm = GateAddNormNetwork(self.hidden_layer_size,
                                                         self.hidden_layer_size,
                                                         self.dropout_rate,
                                                         activation = None)
        
    def build_output_feed_forward(self):
        self.output_feed_forward = torch.nn.Linear(self.hidden_layer_size, 
                                                   self.output_size * len(self.quantiles))
         
    def get_decoder_mask(self, self_attn_inputs):
        """Returns causal mask to apply for self-attention layer.
        Args:
        self_attn_inputs: Inputs to self attention layer to determine mask shape
        """
        len_s = self_attn_inputs.shape[1]
        bs = self_attn_inputs.shape[0]
        mask = torch.cumsum(torch.eye(len_s), 0)
        mask = mask.repeat(bs,1,1).to(torch.float32)

        return mask.to(DEVICE)
    
    def get_tft_embeddings(self, regular_inputs, categorical_inputs):
        # Static input
        if self._static_input_loc:
            static_regular_inputs = [self.regular_var_embeddings[i](regular_inputs[:, 0, i:i + 1]) 
                                    for i in range(self.num_regular_variables)
                                    if i in self._static_input_loc]
            #print('static_regular_inputs')
            #print([print(emb.shape) for emb in static_regular_inputs])
            
            static_categorical_inputs = [self.categorical_var_embeddings[i](categorical_inputs[Ellipsis, i])[:,0,:] 
                                         for i in range(self.num_categorical_variables)
                                         if i + self.num_regular_variables in self._static_input_loc]
            #print('static_categorical_inputs')
            #print([print(emb.shape) for emb in static_categorical_inputs])
            static_inputs = torch.stack(static_regular_inputs + static_categorical_inputs, axis = 1)
        else:
            static_inputs = None
            
        # Target input
        obs_inputs = torch.stack([self.regular_var_embeddings[i](regular_inputs[Ellipsis, i:i + 1])
                                     for i in self._input_obs_loc], axis=-1)
        
        # Observed (a prioir unknown) inputs
        wired_embeddings = []
        for i in range(self.num_categorical_variables):
            if i not in self._known_categorical_input_idx \
            and i not in self._input_obs_loc:
                e = self.categorical_var_embeddings[i](categorical_inputs[:, :, i])
                wired_embeddings.append(e)

        unknown_inputs = []
        for i in range(self.num_regular_variables):
            if i not in self._known_regular_input_idx \
            and i not in self._input_obs_loc:
                e = self.regular_var_embeddings[i](regular_inputs[Ellipsis, i:i + 1])
                unknown_inputs.append(e)
                
        if unknown_inputs + wired_embeddings:
            unknown_inputs = torch.stack(unknown_inputs + wired_embeddings, axis=-1)
        else:
            unknown_inputs = None
            
        # A priori known inputs
        known_regular_inputs = [self.regular_var_embeddings[i](regular_inputs[Ellipsis, i:i + 1])
                                for i in self._known_regular_input_idx
                                if i not in self._static_input_loc]
        #print('known_regular_inputs')
        #print([print(emb.shape) for emb in known_regular_inputs])
        
        known_categorical_inputs = [self.categorical_var_embeddings[i](categorical_inputs[Ellipsis, i])
                                    for i in self._known_categorical_input_idx
                                    if i + self.num_regular_variables not in self._static_input_loc]
       #print('known_categorical_inputs')
       #print([print(emb.shape) for emb in known_categorical_inputs])

        known_combined_layer = torch.stack(known_regular_inputs + known_categorical_inputs, axis=-1)
        
        return unknown_inputs, known_combined_layer, obs_inputs, static_inputs
        
    def forward(self, all_inputs):

        regular_inputs = all_inputs[:, :, :self.num_regular_variables].to(torch.float)
        #print('regular_inputs')
        #print(regular_inputs.shape)
        categorical_inputs = all_inputs[:, :, self.num_regular_variables:].to(torch.long)
        #print('categorical_inputs')
        #print(categorical_inputs.shape)
        
        unknown_inputs, known_combined_layer, obs_inputs, static_inputs \
            = self.get_tft_embeddings(regular_inputs, categorical_inputs)
        
        # Isolate known and observed historical inputs.
        if unknown_inputs is not None:
              historical_inputs = torch.cat([
                  unknown_inputs[:, :self.num_encoder_steps, :],
                  known_combined_layer[:, :self.num_encoder_steps, :],
                  obs_inputs[:, :self.num_encoder_steps, :]
              ], axis=-1)
        else:
              historical_inputs = torch.cat([
                  known_combined_layer[:, :self.num_encoder_steps, :],
                  obs_inputs[:, :self.num_encoder_steps, :]
              ], axis=-1)
                
        #print('historical_inputs')
        #print(historical_inputs.shape)
        
        # Isolate only known future inputs.
        future_inputs = known_combined_layer[:, self.num_encoder_steps:, :]
        #print('future_inputs')
        #print(future_inputs.shape)
              
        #print('static_inputs')
        #print(static_inputs.shape)
        
        static_encoder, sparse_weights = self.static_vsn(static_inputs)
        
        #print('static_encoder')
        #print(static_encoder.shape)
        
        #print('sparse_weights')
        #print(sparse_weights.shape)
        
        static_context_variable_selection = self.static_context_variable_selection_grn(static_encoder)
        #print('static_context_variable_selection')
        #print(static_context_variable_selection.shape)
        static_context_enrichment = self.static_context_enrichment_grn(static_encoder)
        #print('static_context_enrichment')
        #print(static_context_enrichment.shape)
        static_context_state_h = self.static_context_state_h_grn(static_encoder)
        #print('static_context_state_h')
        #print(static_context_state_h.shape)
        static_context_state_c = self.static_context_state_c_grn(static_encoder)
        #print('static_context_state_c')
        #print(static_context_state_c.shape)
        
        historical_features, historical_flags \
        = self.temporal_historical_vsn((historical_inputs,
                                        static_context_variable_selection))
        #print('historical_features')
        #print(historical_features.shape)
        #print('historical_flags')
        #print(historical_flags.shape)
        
        future_features, future_flags \
        = self.temporal_future_vsn((future_inputs,
                                    static_context_variable_selection))
        #print('future_features')
        #print(future_features.shape)
        #print('future_flags')
        #print(future_flags.shape)
        
        history_lstm, (state_h, state_c) \
        = self.historical_lstm(historical_features,
                               (static_context_state_h.unsqueeze(0),
                                static_context_state_c.unsqueeze(0)))
        #print('history_lstm')
        #print(history_lstm.shape)
        #print('state_h')
        #print(state_h.shape)
        #print('state_c')
        #print(state_c.shape)
        
        future_lstm, _ = self.future_lstm(future_features,
                                          (state_h,
                                           state_c))
        #print('future_lstm')
        #print(future_lstm.shape)
        
        # Apply gated skip connection
        input_embeddings = torch.cat((historical_features, future_features), axis=1)
        #print('input_embeddings')
        #print(input_embeddings.shape) 
        
        lstm_layer = torch.cat((history_lstm, future_lstm), axis=1)
        #print('lstm_layer')
        #print(lstm_layer.shape) 
        
        temporal_feature_layer = self.post_seq_encoder_gate_add_norm(lstm_layer, input_embeddings)
        #print('temporal_feature_layer')
        #print(temporal_feature_layer.shape)  
        
        # Static enrichment layers
        expanded_static_context = static_context_enrichment.unsqueeze(1)
        
        enriched = self.static_enrichment((temporal_feature_layer, expanded_static_context))
        #print('enriched')
        #print(enriched.shape)    
        
        # Decoder self attention
        #self.mask = self.get_decoder_mask(enriched)
        #print('enriched')
        #print(enriched.shape)
        x, self_att = self.self_attn_layer(enriched, 
                                           enriched, 
                                           enriched,
                                           mask = self.get_decoder_mask(enriched))
        #print('x')
        #print(x.shape)
        #print('self_att')
        #print(self_att.shape)
        
        x = self.post_attn_gate_add_norm(x, enriched)
        #print('x')
        #print(x.shape)
        
        # Nonlinear processing on outputs
        decoder = self.GRN_positionwise(x)
        #print('decoder')
        #print(decoder.shape)
        
        # Final skip connection
        transformer_layer = self.post_tfd_gate_add_norm(decoder, temporal_feature_layer)
        #print('transformer_layer')
        #print(transformer_layer.shape)
        
        outputs = self.output_feed_forward(transformer_layer[Ellipsis, self.num_encoder_steps:, :])
        #print('outputs')
        #print(outputs.shape)
        
        #ipdb.set_trace()
        
        return outputs
    
    def loss(self, y_hat, y):
        return self.train_criterion.apply(y_hat, y)
    
    def test_loss(self, y_hat, y):
        return self.test_criterion.apply(y_hat, y, self.quantiles[1])
    
    def training_step(self, batch, batch_nb):
        x, y, _ = batch
        
        x = x.to(torch.float)
        y = y.to(torch.float)
#         print('y')
#         print(y.shape)
        y_hat = self.forward(x)
#         print('y_hat')
#         print(y_hat.shape)
        loss = self.loss(y_hat, torch.cat([y, y, y], dim = -1))
        #print(loss.shape)
        tensorboard_logs = {'train_loss': loss}
        return {'loss': loss, 'log': tensorboard_logs}
    
    def validation_step(self, batch, batch_nb):
        x, y, _ = batch
        x = x.to(torch.float)
        y = y.to(torch.float)
        y_hat = self.forward(x)
        #print(y_hat.shape)
        #print(torch.cat([y, y, y], dim = -1).shape)
        loss = self.loss(y_hat, torch.cat([y, y, y], dim = -1))
        #print(loss)
        return {'val_loss': loss}
    
    def validation_end(self, outputs):
        avg_loss = torch.stack([x['val_loss'] for x in outputs]).mean()
        tensorboard_logs = {'val_loss': avg_loss}
        return {'avg_val_loss': avg_loss, 'log': tensorboard_logs}
    
    def test_step(self, batch, batch_idx):
        # OPTIONAL
        x, y, _ = batch
        x = x.to(torch.float)
        y = y.to(torch.float)
        y_hat = self.forward(x)
        return {'test_loss': self.test_loss(y_hat[Ellipsis, 1], y[Ellipsis, 0])}

    def test_end(self, outputs):
        # OPTIONAL
        avg_loss = torch.stack([x['test_loss'] for x in outputs]).mean()
        tensorboard_logs = {'test_loss': avg_loss}
        return {'avg_test_loss': avg_loss, 'log': tensorboard_logs}
    
    def configure_optimizers(self):
        # REQUIRED
        # can return multiple optimizers and learning_rate schedulers
        # (LBFGS it is automatically supported, no need for closure function)
        return [torch.optim.Adam(self.parameters(), lr=self.learning_rate)]
    
    def plot_grad_flow(self, named_parameters):
        ave_grads = []
        layers = []
        for name, p in named_parameters:
            if p.grad is not None:
                if (p.requires_grad) and ("bias" not in name):
                    layers.append(name)
                    ave_grads.append(p.grad.abs().mean())
                    self.logger.experiment.add_histogram(tag=name, values=p.grad,
                                                         global_step=self.trainer.global_step)
            else:
                 print('{} - {}'.format(name, p.requires_grad))
            
        plt.plot(ave_grads, alpha=0.3, color="b")
        plt.hlines(0, 0, len(ave_grads), linewidth=1, color="k" )
        plt.xticks(list(range(0,len(ave_grads), 1)), layers, rotation='vertical')
        plt.xlim(left=0, right=len(ave_grads))
        plt.xlabel("Layers")
        plt.ylabel("average gradient")
        plt.title("Gradient flow")
        plt.grid(True)
        plt.rcParams["figure.figsize"] = (20, 5)
    
    def on_after_backward(self):
        # example to inspect gradient information in tensorboard
        if self.trainer.global_step % 25 == 0:  
            self.plot_grad_flow(self.named_parameters())
    
    def train_dataloader(self):
        # REQUIRED
        return DataLoader(train_dataset, batch_size = self.minibatch_size, shuffle=True, drop_last=True, num_workers=1)

    def val_dataloader(self):
        # OPTIONAL
        return DataLoader(valid_dataset, batch_size = self.minibatch_size, shuffle=True, drop_last=True, num_workers=1)
    
    def test_dataloader(self):
        # OPTIONAL
        return DataLoader(test_dataset, batch_size = self.minibatch_size, shuffle=True, drop_last=True, num_workers=1)